In [271]:
# Web-scraping for dataset setup
from bs4 import BeautifulSoup
import requests

In [272]:
# Import url and then perform scraping to extract the list of categories of doctors/physicians
base_url = 'https://www.miodottore.it/categorie' # Set the link baseline
headers = {
    "User-Agent": "Mozilla/5.0"  # To mimic a browser and avoid bot blocking
}
page = requests.get(base_url, headers=headers)
soup = BeautifulSoup(page.content, 'html.parser')

In [273]:
# Extract the categories, get the text in the right class, sub-class
categories_list = soup.select("h3.flex-grow-1.mb-0 a.text-muted")
# Extract the location detail pages from each category
categories_locations = soup.select("div.mt-1 a.text-muted")

In [274]:
# Create a list to hold the category names, main url, location url
category_list_data = [] # Empty list
# Print the list of categories, urls, locations
for category, location_url in zip(categories_list, categories_locations):
    # Extract the category name and URL
    category_name = category.get_text(strip=True) # Get only text part
    category_url = category['href'] # The href part of the category
    main_url = f"https://www.miodottore.it{category_url}"
    
    # Append the data as a tuple to the list
    category_list_data.append({
        'name': category_name,
        'main_page': main_url,
        'location_page': location_url['href'] # Extract the href from the location URL
    })

In [275]:
category_list_data

[{'name': 'Agopuntori',
  'main_page': 'https://www.miodottore.it/agopuntore',
  'location_page': 'https://www.miodottore.it/categorie/nel-dettaglio/agopuntore'},
 {'name': 'Allergologi',
  'main_page': 'https://www.miodottore.it/allergologo',
  'location_page': 'https://www.miodottore.it/categorie/nel-dettaglio/allergologo'},
 {'name': 'Analisti Clinici',
  'main_page': 'https://www.miodottore.it/analista-clinico',
  'location_page': 'https://www.miodottore.it/categorie/nel-dettaglio/analista-clinico'},
 {'name': 'Anatomopatologi',
  'main_page': 'https://www.miodottore.it/anatomopatologo',
  'location_page': 'https://www.miodottore.it/categorie/nel-dettaglio/anatomopatologo'},
 {'name': 'Andrologi',
  'main_page': 'https://www.miodottore.it/andrologo',
  'location_page': 'https://www.miodottore.it/categorie/nel-dettaglio/andrologo'},
 {'name': 'Anestesisti',
  'main_page': 'https://www.miodottore.it/anestesista',
  'location_page': 'https://www.miodottore.it/categorie/nel-dettaglio/a

In [276]:
# Find all specific city links from the location page
for entry in category_list_data:
    main_url = entry['main_page'] # Get the main page URL (Found at the beginning of all links)
    location_page_url = entry['location_page'] # Get the location detail page URL, collective not specific cities
    headers = {
    "User-Agent": "Mozilla/5.0"  # To mimic a browser and avoid bot blocking
    }
    # Derive the new page and soup object for the location page
    location_page = requests.get(location_page_url, headers=headers)
    location_soup = BeautifulSoup(location_page.content, 'html.parser')
    # Extract the specific city links from the location page
    city_links = location_soup.select("li.col-md-6 a")
    city_link_list = [f'https://www.miodottore.it{link["href"]}' for link in city_links]
    # Add the city links to the entry
    entry['city_links'] = city_link_list

In [277]:
# Sanity check
category_list_data

[{'name': 'Agopuntori',
  'main_page': 'https://www.miodottore.it/agopuntore',
  'location_page': 'https://www.miodottore.it/categorie/nel-dettaglio/agopuntore',
  'city_links': ['https://www.miodottore.it/agopuntore/abbadia-alpina',
   'https://www.miodottore.it/agopuntore/acerra',
   'https://www.miodottore.it/agopuntore/acilia',
   'https://www.miodottore.it/agopuntore/acireale',
   'https://www.miodottore.it/agopuntore/acqui-terme',
   'https://www.miodottore.it/agopuntore/agliana',
   'https://www.miodottore.it/agopuntore/airola',
   'https://www.miodottore.it/agopuntore/alba',
   'https://www.miodottore.it/agopuntore/albano-laziale',
   'https://www.miodottore.it/agopuntore/albignasego',
   'https://www.miodottore.it/agopuntore/albino',
   'https://www.miodottore.it/agopuntore/alessandria',
   'https://www.miodottore.it/agopuntore/ancona',
   'https://www.miodottore.it/agopuntore/angri',
   'https://www.miodottore.it/agopuntore/antegnate',
   'https://www.miodottore.it/agopuntore

In [278]:
# Check that we get doctor's urls for a specific city (Sanity check 2)
doctor_urls = []
city_page = requests.get('https://www.miodottore.it/anestesista/abano-terme', headers= headers)
city_soup = BeautifulSoup(city_page.content, 'html.parser')
doctor_links = city_soup.select("h3.h4.mb-0.flex-wrap a.text-body")
doctor_urls.extend([f'{link["href"]}' for link in doctor_links])
doctor_urls


['https://www.miodottore.it/vincenzo-tegazzin/anestesista/padova',
 'https://www.miodottore.it/ariadna-tudurachi/anestesista/albignasego',
 'https://www.miodottore.it/giorgio-davia/anestesista/selvazzano-dentro',
 'https://www.miodottore.it/dorotea-magaldi/anestesista-agopuntore/padova',
 'https://www.miodottore.it/cinzia-favaro/terapista-del-dolore/vicenza',
 'https://www.miodottore.it/strutture/fisiotecnik-s-r-l-2',
 'https://www.miodottore.it/giandomenico-babbolin/anestesista-medico-di-base-dentista/puegnago-sul-garda',
 'https://www.miodottore.it/strutture/centro-medico-serena-2',
 'https://www.miodottore.it/mario-trivellato/anestesista-cardiologo-internista/padova',
 'https://www.miodottore.it/massimo-rossato/agopuntore-anestesista-terapista-del-dolore/padova',
 'https://www.miodottore.it/gianfranco-sattin/anestesista/padova',
 'https://www.miodottore.it/angela-menegazzo/anestesista/padova',
 'https://www.miodottore.it/ivaldo-polo/medico-di-base-anestesista-medico-dello-sport/aban

In [ ]:
# Now, we will collect doctor's page url from each city link
# Original code (Taking too long)
# doctor_urls = []  # List to hold all doctor URLs
#for entry in category_list_data:
#    city_links = entry['city_links']  # Get the list of city links
#    headers = {
#            "User-Agent": "Mozilla/5.0"  # To mimic a browser and avoid bot blocking
#        }
#    for city_link in city_links:
        
        # Fetch the page for the specific city
#        city_page = requests.get(city_link, headers=headers)
#        city_soup = BeautifulSoup(city_page.content, 'html.parser')
        
        # Extract doctor links from the city page
#       doctor_links = city_soup.select("h3.h4.mb-0.flex-wrap a.text-body")
#       doctor_urls.extend([f'{link["href"]}' for link in doctor_links])


In [279]:
# Define a function to fetch doctor links from a city URL using threading
from concurrent.futures import ThreadPoolExecutor, as_completed

import time, random

def fetch_doctor_links(city_url):
    headers = {
        "User-Agent": "Mozilla/5.0"
    }
    try:
        time.sleep(random.uniform(0.5, 1.2))  # Add delay per request
        resp = requests.get(city_url, headers=headers, timeout=10)
        soup = BeautifulSoup(resp.content, 'html.parser')
        doctor_links = soup.select("h3.h4.mb-0 a.text-body")

        if len(doctor_links) == 0:
            print(f"⚠️ No doctor links found for: {city_url}")
        return [f"{link['href']}" for link in doctor_links]

    except Exception as e:
        print(f"❌ Failed: {city_url}\nReason: {e}")
        return []



In [18]:
# Multithreaded scraping to fetch doctor links from all city pages
from tqdm import tqdm  # optional, for progress bar

doctor_urls = []  # master list

for entry in tqdm(category_list_data):
    city_links = entry['city_links']
    
    entry_doctor_urls = []
    with ThreadPoolExecutor(max_workers= 5) as executor:
        futures = [executor.submit(fetch_doctor_links, city) for city in city_links]
        for future in as_completed(futures):
            entry_doctor_urls.extend(future.result())

    entry["doctor_urls"] = entry_doctor_urls
    doctor_urls.extend(entry_doctor_urls)  # As I want a full list


  1%|          | 1/96 [03:37<5:44:31, 217.59s/it]

⚠️ No doctor links found for: https://www.miodottore.it/allergologo/san-vito-di-cadore


  5%|▌         | 5/96 [16:54<5:47:54, 229.39s/it]

❌ Failed: https://www.miodottore.it/anestesista/aquileia
Reason: Response ended prematurely


 23%|██▎       | 22/96 [1:15:01<3:27:24, 168.17s/it]

...

 93%|█████████▎| 89/96 [7:55:46<24:00, 205.76s/it]

⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/adelfia
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/casirate-d-adda
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/castello-d-agogna
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/castellammare-di-stabia
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/catania
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/cecina
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/cormons
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/cortemaggiore
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/fiorenzuola-d-arda
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/isola-della-scala
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/l-aquila
⚠️ No doctor links found for: https:/

 94%|█████████▍| 90/96 [7:56:30<15:43, 157.32s/it]

⚠️ No doctor links found for: https://www.miodottore.it/tecnico-radiologo/viterbo
⚠️ No doctor links found for: https://www.miodottore.it/tecnico-sanitario/monselice


100%|██████████| 96/96 [8:17:54<00:00, 311.19s/it]


In [284]:
doctor_urls

['https://www.miodottore.it/vincenzo-tegazzin/anestesista/padova',
 'https://www.miodottore.it/ariadna-tudurachi/anestesista/albignasego',
 'https://www.miodottore.it/giorgio-davia/anestesista/selvazzano-dentro',
 'https://www.miodottore.it/dorotea-magaldi/anestesista-agopuntore/padova',
 'https://www.miodottore.it/cinzia-favaro/terapista-del-dolore/vicenza',
 'https://www.miodottore.it/strutture/fisiotecnik-s-r-l-2',
 'https://www.miodottore.it/giandomenico-babbolin/anestesista-medico-di-base-dentista/puegnago-sul-garda',
 'https://www.miodottore.it/strutture/centro-medico-serena-2',
 'https://www.miodottore.it/mario-trivellato/anestesista-cardiologo-internista/padova',
 'https://www.miodottore.it/massimo-rossato/agopuntore-anestesista-terapista-del-dolore/padova',
 'https://www.miodottore.it/gianfranco-sattin/anestesista/padova',
 'https://www.miodottore.it/angela-menegazzo/anestesista/padova',
 'https://www.miodottore.it/ivaldo-polo/medico-di-base-anestesista-medico-dello-sport/aban

In [20]:
# Save the doctor URLS list to a file, to make it usable later
import json
# Save the doctor URLs to a JSON file
with open('doctor_urls.json', 'w') as f:
    json.dump(doctor_urls, f, indent=4)

In [285]:
# Load the doctor URLs from the JSON file
import json
with open('doctor_urls.json', 'r') as f:
    loaded_doctor_urls = json.load(f)

In [288]:
# Check the total number of doctor URLS collected
len(set(loaded_doctor_urls))

121636

In [303]:
# Sanity check for specific doctor URL, found in doctor list or not?
target_url = 'https://www.miodottore.it/maria-rita-bongiorno/dermatologo-venereologo/palermo'

found = False
if target_url in loaded_doctor_urls:
    print(f"✅ Found")
    found = True
else:
    print("❌ Not found in any category")


✅ Found


In [304]:
name_parts = soup.select("div.unified-doctor-header-info__name span") if soup.select("div.unified-doctor-header-info__name span") else None
# Combine name parts
name = " ".join(part.get_text(strip = True) for part in name_parts) if name_parts else None


In [305]:
name

'Dr. Valentina Bellato'

In [313]:
# Check the location, review, and more extraction before starting entire loops
import requests
from bs4 import BeautifulSoup
headers = {
        "User-Agent": "Mozilla/5.0"
    }
resp = requests.get(target_url, headers=headers)
soup = BeautifulSoup(resp.content, 'html.parser')
# Extracting the required details
location = soup.select_one("div.mb-0-25 p")

In [314]:
import re

location_tag = soup.select_one('p[data-test-id="doctor-locations"]')
if location_tag:
    match = re.search(r'\b[A-Z][a-z]+\b', location_tag.get_text())
    location_text = match.group(0) if match else None
else:
    location_text = None


In [315]:
location_text

'Palermo'

In [309]:
# Extracting recensioni (reviews)
rating = soup.select_one('div.rating.rating-lg')
if rating:
    rating_score = rating['data-score']
else:
    rating_score = None

In [310]:
rating_score

'5'

In [323]:
# Check total reviews for specific urls
number_of_reviews = soup.select_one('div.d-flex.justify-content-between.flex-column.flex-sm-row p.mb-0')
if number_of_reviews:
    total_reviews = number_of_reviews.get_text(strip=True).split(" ")[0]
else:
    total_reviews = None

In [324]:
number_of_reviews

<p class="mb-0">10 recensioni</p>

In [325]:
total_reviews

'10'

In [39]:
# Check available services (`Prestazioni`)
services = soup.select('li[data-id="service-item"]')
available_services = {}

for service in services:
    name_tag = service.select_one('h3[itemprop="availableService"]')
    price_tag = service.select_one('div.d-flex div.mr-1')  # gets the first <font> which contains the price

    name = name_tag.get_text(strip=True) if name_tag else None # get one value
    price = price_tag.get_text(strip=True) if price_tag else None # get one value

    if name:
        available_services[name] = price.replace('\xa0', ' ') if price else None # Cut the non-breaking space character



In [41]:
available_services

{}

In [42]:
# Try to get all categoy of eah doctor
# Find the container that holds specializations
# Select specialization tags
specialization_list = []
specialization_tags = soup.select('a.text-base-size.font-weight-normal.text-body')

# Extract and clean the text, excluding "Altro"
if specialization_tags:
    specializations = [
        tag.get_text(strip=True)
        for tag in specialization_tags
        if tag.get_text(strip=True).lower() != 'altro'
    ]

    # Join into a string
    specialization_str = ', '.join(specializations)
    specialization_list.append(specialization_str)
else:
    specialization_list = None


In [43]:
specialization_list

['Agopuntore, Terapeuta, Anestesista']

In [44]:
# Select all <ul> elements with the desired class
ul_elements = soup.select('ul.toggleable-list.pl-2.mb-0')

# Dictionary to hold results by id
categorized_data = {}

for ul in ul_elements:
    ul_id = ul.get('id')
    if ul_id:
        items = [li.get_text(strip=True) for li in ul.find_all('li')]
        categorized_data[ul_id] = items

# Example access
# print(categorized_data['disease'])  # will show list of disease items
# print(categorized_data.keys())      # all section names (ids)


In [45]:
categorized_data

{}

In [ ]:
#from tqdm import tqdm  # optional, for progress bar (Manually, slow)
#from bs4 import BeautifulSoup
#import requests
#doctor_names = []  # List to hold doctor names
#for doctor_url in tqdm(loaded_doctor_urls):
#    resp = requests.get(doctor_url, headers={"User-Agent": "Mozilla/5.0"})
#    soup = BeautifulSoup(resp.content, 'html.parser')
#    # Extracting the required details
#    name_parts = soup.select("div.unified-doctor-header-info__name span") if soup.select("div.unified-doctor-header-info__name span") else None
#    # Combine name parts
#    name = " ".join(part.get_text(strip = True) for part in name_parts) if name_parts else None
#    # extend the list with the name
#    doctor_names.append(name)

Full Function for Miodottore-Scraping

In [ ]:
# Extract the doctor's data(Name, Location, Recensioni, Prestazioni, Esperienze)
# The last scraping part is getting all these details from each doctor's page
import time, random
import requests
from bs4 import BeautifulSoup
import re
def fetch_doctor_details(doctor_url):
    headers = {
        "User-Agent": "Mozilla/5.0"
    }
    try:
        time.sleep(random.uniform(0.5, 1.2))  # Add delay per request
        resp = requests.get(doctor_url, headers=headers, timeout=10)
        soup = BeautifulSoup(resp.content, 'html.parser')

        # Extracting the name details
        name_parts = soup.select("div.unified-doctor-header-info__name span") if soup.select("div.unified-doctor-header-info__name span") else None
        # Combine name parts
        name = " ".join(part.get_text(strip = True) for part in name_parts) if name_parts else None

        # Extract category and specialization
        # Try to get all categoy of eah doctor
        # Find the container that holds specializations
        # Select specialization tags
        specialization_list = []
        specialization_tags = soup.select('a.text-base-size.font-weight-normal.text-body')

        # Extract and clean the text, excluding "Altro"
        if specialization_tags:
            specializations = [
                tag.get_text(strip=True)
                for tag in specialization_tags
                if tag.get_text(strip=True).lower() != 'altro']

            # Join into a string
            specialization_str = ', '.join(specializations)
            specialization_list.append(specialization_str)
        else:
            specialization_list = None
        
        # Now extract the location
        location_tag = soup.select_one('p[data-test-id="doctor-locations"]')
        if location_tag:
            match = re.search(r'\b[A-Z][a-z]+\b', location_tag.get_text())
            location_text = match.group(0) if match else None
        else:
            location_text = None    
        
        # Extracting reviews (`Recensioni`)
        rating = soup.select_one('div.rating.rating-lg')
        if rating:
            rating_score = rating['data-score']
        else:
            rating_score = None

        # Also extract number of reviews
        number_of_reviews = soup.select_one('div.d-flex.justify-content-between.flex-column.flex-sm-row p.mb-0')
        if number_of_reviews:
            total_reviews = number_of_reviews.get_text(strip=True).split(" ")[0]
        else:
            total_reviews = None

        # Extract all available services (`Prestazioni`)
        # Check available services (`Prestazioni`)
        services = soup.select('li[data-id="service-item"]')
        available_services = {}

        for service in services:
            name_tag = service.select_one('h3[itemprop="availableService"]')
            price_tag = service.select_one('div.d-flex div.mr-1')  # gets the first <font> which contains the price

            name_service = name_tag.get_text(strip=True) if name_tag else None # get one value
            price = price_tag.get_text(strip=True) if price_tag else None # get one value

            if name_service:
                available_services[name_service] = price.replace('\xa0', ' ') if price else None # Cut the non-breaking space character

        # Extract Espirienze
        # Select all <ul> elements with the desired class
        ul_elements = soup.select('ul.toggleable-list.pl-2.mb-0')

        # Dictionary to hold results by id
        categorized_data = {}

        for ul in ul_elements:
            ul_id = ul.get('id')
            if ul_id:
                items = [li.get_text(strip=True) for li in ul.find_all('li')]
                categorized_data[ul_id] = items

        return {
            'name': name,
            'categories': specialization_list,
            'url': doctor_url,
            'location': location_text,
            'rating': rating_score,
            'number_of_reviews': total_reviews,
            'prestazioni': available_services,
            'espierienze': categorized_data
        }

    except Exception as e:
        print(f"❌ Failed to fetch details for: {doctor_url}\nReason: {e}")
        return None



In [59]:
# Multithreaded scraping to fetch doctor details from all doctor URLs, check small portion of loaded_doctor_urls first
 # For testing, use a small portion  
from tqdm import tqdm  # optional, for progress bar
from concurrent.futures import ThreadPoolExecutor, as_completed
small_doctor_urls = loaded_doctor_urls[900000:]  # Take first 10 URLs for testing
doctor_details = []  # master list
with ThreadPoolExecutor(max_workers= 5) as executor:
    futures = [executor.submit(fetch_doctor_details, url) for url in small_doctor_urls]
    for future in tqdm(as_completed(futures), total=len(small_doctor_urls)):
        doctor_details.append(future.result())

  1%|          | 1789/177906 [14:51<223:55:01,  4.58s/it]

❌ Failed to fetch details for: https://www.miodottore.it/teresa-colaiacovo/psicologo-sessuologo-psicoterapeuta/genova
Reason: HTTPSConnectionPool(host='www.miodottore.it', port=443): Read timed out.


  3%|▎         | 4731/177906 [38:35<139:37:37,  2.90s/it]

❌ Failed to fetch details for: https://www.miodottore.it/dario-agradi-2/psicologo-clinico-psicologo/sesto-san-giovanni
Reason: HTTPSConnectionPool(host='www.miodottore.it', port=443): Read timed out. (read timeout=10)


  6%|▌         | 10659/177906 [1:25:27<286:31:54,  6.17s/it]

...

 99%|█████████▉| 175864/177906 [22:59:22<17:13,  1.98it/s]  

❌ Failed to fetch details for: https://www.miodottore.it/umberto-alberio/internista/vimercate
Reason: Response ended prematurely


 99%|█████████▉| 176924/177906 [23:07:48<1:56:34,  7.12s/it]

❌ Failed to fetch details for: https://www.miodottore.it/luca-rubino/dermatologo/capurso
Reason: HTTPSConnectionPool(host='www.miodottore.it', port=443): Read timed out. (read timeout=10)


100%|██████████| 177906/177906 [23:14:42<00:00,  2.13it/s]  


In [60]:
doctor_details

[{'name': 'Dott.ssa Giulia Pedrotti ',
  'categories': ['Psicologo, Neuropsicologo'],
  'url': 'https://www.miodottore.it/giulia-pedrotti/psicologo-neuropsicologo/verona',
  'location': 'Verona',
  'rating': None,
  'number_of_reviews': None,
  'prestazioni': {'Colloquio psicologico': None,
   'Consulenza online': None,
   'Consulenza psicologica': None,
   'Orientamento scolastico': None,
   'Riabilitazione': None,
   'Sostegno psicologico': None,
   'Sostegno psicologico adolescenti': None,
   'Valutazione neuropsicologica': None},
  'espierienze': {'expertIn': ['Psicologia clinica', 'Neuropsicologia']}},
 {'name': 'Davide Cordioli ',
  'categories': ['Psicologo'],
  'url': 'https://www.miodottore.it/davide-cordioli-2/psicologo/verona',
  'location': 'Verona',
  'rating': None,
  'number_of_reviews': None,
  'prestazioni': {'Colloquio psicologico': 'Da 50 €',
   'Consulenza psicologica': 'Da 50 €',
   'Colloquio psicologico clinico': '50 €',
   'Prima Visita': '50 €',
   'Psicoterapi

In [61]:
 # Save the doctor details to a JSON file
import json
with open('doctor_details_example_12.json', 'w') as f:
    json.dump(doctor_details, f, indent=4)

In [62]:
# Import doctor details from the JSON file
import json
with open('doctor_details_example_12.json', 'r') as f:
    doctor_details_example_12 = json.load(f)

In [63]:
doctor_details_example_12[-1]

{'name': 'Prof.ssa Maria Rita Bongiorno ',
 'categories': ['Dermatologo, Venereologo'],
 'url': 'https://www.miodottore.it/maria-rita-bongiorno/dermatologo-venereologo/palermo',
 'location': 'Palermo',
 'rating': '5',
 'number_of_reviews': 'Recensioni',
 'prestazioni': {'Visita dermatologica': '220 €',
  'Visita a domicilio': '400 €',
  'Visita di controllo': '130 €',
  'Visita venereologica': '220 €'},
 'espierienze': {'expertIn': ['Dermatologia e venereologia'],
  'disease': ['Acne',
   'Verruche',
   'Alopecia',
   'Dermatite atopica',
   'Psoriasi',
   'Micosi',
   'Herpes zoster',
   'Malattie sessualmente trasmissibili',
   'Cheratosi attinica',
   'Malattie bollose'],
  'practice': ['.'],
  'publication': ['.'],
  'school': ['Università degli Studi di Palermo'],
  'prize': ['.']}}

In [64]:
len(doctor_details_example_12)  # Check the total number of doctor details collected

177906

In [65]:
import pandas as pd
import json

processed = []
for d in doctor_details_example_12:
    if d is None:
        continue  # Skip bad entries
    
    # Convert nested structures to JSON strings for CSV compatibility
    row = {}
    for k, v in d.items():
        if isinstance(v, (list, dict)):
            row[k] = json.dumps(v, ensure_ascii=False)
        else:
            row[k] = v
    processed.append(row)

df = pd.DataFrame(processed)
df.to_csv("doctor_details_part_10.csv", index=False)


Finish Web Scraping

In [291]:
# Merge all parts of the doctor details CSV files into one
import pandas as pd
import glob # glob is used to find all the pathnames matching a specified pattern

# Get all CSV files in the current directory
csv_files = glob.glob("doctor_details_part_*.csv") # read all parts 

# Read and concatenate all CSV files into a single DataFrame
df_list = [pd.read_csv(file) for file in csv_files]
df = pd.concat(df_list, ignore_index=True)

# Save the final DataFrame to a CSV file
df.to_csv("doctor_details_final.csv", index=False)

Data Cleaning

In [292]:
# Download DF from doctor_details_final.csv
import pandas as pd
# Load the final DataFrame from the CSV file
df = pd.read_csv("doctor_details_final.csv")
df.head()  # Display the first few rows of the DataFrame

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/2645359556.py:4: DtypeWarning: Columns (5) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("doctor_details_final.csv")


name    categories  \
0        Dr. Antonio Iasi  ["Pediatra"]   
1  Dr. Piera Angela Negro  ["Pediatra"]   
2           Angela Russo   ["Pediatra"]   
3    Dott. Ivana Stapane   ["Pediatra"]   
4  Dr. Salvatore Fulgido   ["Pediatra"]   

                                                 url   location  rating  \
0  https://www.miodottore.it/antonio-iasi/pediatr...    Neviano     NaN   
1  https://www.miodottore.it/piera-angela-negro/p...  Gallipoli     NaN   
2  https://www.miodottore.it/angela-russo-2/pedia...   Galatone     NaN   
3  https://www.miodottore.it/ivana-stapane/pediat...   Galatone     NaN   
4  https://www.miodottore.it/salvatore-fulgido/pe...     Alezio     NaN   

  number_of_reviews prestazioni espierienze  
0               NaN          {}          {}  
1               NaN          {}          {}  
2               NaN          {}          {}  
3               NaN          {}          {}  
4               NaN          {}          {}

In [2]:
df

name  \
0                            Dr. Antonio Iasi   
1                      Dr. Piera Angela Negro   
2                               Angela Russo    
3                        Dott. Ivana Stapane    
4                      Dr. Salvatore Fulgido    
...                                       ...   
1077640              Dott.ssa Roberta Alaimo    
1077641  Dott.ssa Ninfa Alessandra Giacalone    
1077642            Dott.ssa Francesca Todaro    
1077643                                   NaN   
1077644        Prof.ssa Maria Rita Bongiorno    

                                      categories  \
0                                   ["Pediatra"]   
1                                   ["Pediatra"]   
2                                   ["Pediatra"]   
3                                   ["Pediatra"]   
4                                   ["Pediatra"]   
...                                          ...   
1077640  ["Dermatologo, Venereologo, Tricologo"]   
1077641      ["Urologo, Andrologo, Venereologo"]   
1077642             ["Dermatologo, Venereologo"]   
1077643                                      NaN   
1077644             ["Dermatologo, Venereologo"]   

                                                       url   location  rating  \
0        https://www.miodottore.it/antonio-iasi/pediatr...    Neviano     NaN   
1        https://www.miodottore.it/piera-angela-negro/p...  Gallipoli     NaN   
2        https://www.miodottore.it/angela-russo-2/pedia...   Galatone     NaN   
3        https://www.miodottore.it/ivana-stapane/pediat...   Galatone     NaN   
4        https://www.miodottore.it/salvatore-fulgido/pe...     Alezio     NaN   
...                                                    ...        ...     ...   
1077640  https://www.miodottore.it/roberta-alaimo/derma...    Palermo     5.0   
1077641  https://www.miodottore.it/ninfa-alessandra-gia...    Palermo     5.0   
1077642  https://www.miodottore.it/francesca-todaro-3/d...    Palermo     5.0   
1077643   https://www.miodottore.it/strutture/mediclinic-2        NaN     5.0   
1077644  https://www.miodottore.it/maria-rita-bongiorno...    Palermo     5.0   

        number_of_reviews                                        prestazioni  \
0                     NaN                                                 {}   
1                     NaN                                                 {}   
2                     NaN                                                 {}   
3                     NaN                                                 {}   
4                     NaN                                                 {}   
...                   ...                                                ...   
1077640        Recensioni  {"Prima visita dermatologica": "Da 70 €", "Inf...   
1077641        Recensioni  {"Visita urologica": null, "Visita di controll...   
1077642        Recensioni  {"Prima visita dermatologica": "100 €", "Visit...   
1077643               NaN                                                 {}   
1077644        Recensioni  {"Visita dermatologica": "220 €", "Visita a do...   

                                               espierienze  
0                                                       {}  
1                                                       {}  
2                                                       {}  
3                                                       {}  
4                                                       {}  
...                                                    ...  
1077640  {"expertIn": ["Dermatologia e venereologia"], ...  
1077641  {"expertIn": ["Andrologia", "Urologia", "Medic...  
1077642  {"expertIn": ["Dermatologia e venereologia"], ...  
1077643                                                 {}  
1077644  {"expertIn": ["Dermatologia e venereologia"], ...  

[1077645 rows x 8 columns]

In [3]:
# Clean the doctor csv file by eliminating all rows that have no name, location, or url
df_cleaned_1 = df.dropna(subset=['name'], ignore_index=True)  # Drop rows where 'name' is NaN
df_cleaned_1


name  \
0                           Dr. Antonio Iasi   
1                     Dr. Piera Angela Negro   
2                              Angela Russo    
3                       Dott. Ivana Stapane    
4                     Dr. Salvatore Fulgido    
...                                      ...   
994773               Dott.ssa Elena Mazzola    
994774              Dott.ssa Roberta Alaimo    
994775  Dott.ssa Ninfa Alessandra Giacalone    
994776            Dott.ssa Francesca Todaro    
994777        Prof.ssa Maria Rita Bongiorno    

                                     categories  \
0                                  ["Pediatra"]   
1                                  ["Pediatra"]   
2                                  ["Pediatra"]   
3                                  ["Pediatra"]   
4                                  ["Pediatra"]   
...                                         ...   
994773             ["Dermatologo, Venereologo"]   
994774  ["Dermatologo, Venereologo, Tricologo"]   
994775      ["Urologo, Andrologo, Venereologo"]   
994776             ["Dermatologo, Venereologo"]   
994777             ["Dermatologo, Venereologo"]   

                                                      url   location  rating  \
0       https://www.miodottore.it/antonio-iasi/pediatr...    Neviano     NaN   
1       https://www.miodottore.it/piera-angela-negro/p...  Gallipoli     NaN   
2       https://www.miodottore.it/angela-russo-2/pedia...   Galatone     NaN   
3       https://www.miodottore.it/ivana-stapane/pediat...   Galatone     NaN   
4       https://www.miodottore.it/salvatore-fulgido/pe...     Alezio     NaN   
...                                                   ...        ...     ...   
994773  https://www.miodottore.it/elena-mazzola/dermat...    Palermo     5.0   
994774  https://www.miodottore.it/roberta-alaimo/derma...    Palermo     5.0   
994775  https://www.miodottore.it/ninfa-alessandra-gia...    Palermo     5.0   
994776  https://www.miodottore.it/francesca-todaro-3/d...    Palermo     5.0   
994777  https://www.miodottore.it/maria-rita-bongiorno...    Palermo     5.0   

       number_of_reviews                                        prestazioni  \
0                    NaN                                                 {}   
1                    NaN                                                 {}   
2                    NaN                                                 {}   
3                    NaN                                                 {}   
4                    NaN                                                 {}   
...                  ...                                                ...   
994773        Recensioni  {"Visita dermatologica": "100 €", "Crioterapia...   
994774        Recensioni  {"Prima visita dermatologica": "Da 70 €", "Inf...   
994775        Recensioni  {"Visita urologica": null, "Visita di controll...   
994776        Recensioni  {"Prima visita dermatologica": "100 €", "Visit...   
994777        Recensioni  {"Visita dermatologica": "220 €", "Visita a do...   

                                              espierienze  
0                                                      {}  
1                                                      {}  
2                                                      {}  
3                                                      {}  
4                                                      {}  
...                                                   ...  
994773  {"expertIn": ["Dermatologia e venereologia"], ...  
994774  {"expertIn": ["Dermatologia e venereologia"], ...  
994775  {"expertIn": ["Andrologia", "Urologia", "Medic...  
994776  {"expertIn": ["Dermatologia e venereologia"], ...  
994777  {"expertIn": ["Dermatologia e venereologia"], ...  

[994778 rows x 8 columns]

In [4]:
# Separate the name column into names and prefixes
df_cleaned_1[['prefix', 'name']] = df_cleaned_1['name'].str.split(' ', n = 1, expand=True) # expand=True creates new columns
df_cleaned_1

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/1959293337.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_1[['prefix', 'name']] = df_cleaned_1['name'].str.split(' ', n = 1, expand=True) # expand=True creates new columns


name                               categories  \
0                      Antonio Iasi                             ["Pediatra"]   
1                Piera Angela Negro                             ["Pediatra"]   
2                            Russo                              ["Pediatra"]   
3                    Ivana Stapane                              ["Pediatra"]   
4                Salvatore Fulgido                              ["Pediatra"]   
...                             ...                                      ...   
994773               Elena Mazzola              ["Dermatologo, Venereologo"]   
994774              Roberta Alaimo   ["Dermatologo, Venereologo, Tricologo"]   
994775  Ninfa Alessandra Giacalone       ["Urologo, Andrologo, Venereologo"]   
994776            Francesca Todaro              ["Dermatologo, Venereologo"]   
994777        Maria Rita Bongiorno              ["Dermatologo, Venereologo"]   

                                                      url   location  rating  \
0       https://www.miodottore.it/antonio-iasi/pediatr...    Neviano     NaN   
1       https://www.miodottore.it/piera-angela-negro/p...  Gallipoli     NaN   
2       https://www.miodottore.it/angela-russo-2/pedia...   Galatone     NaN   
3       https://www.miodottore.it/ivana-stapane/pediat...   Galatone     NaN   
4       https://www.miodottore.it/salvatore-fulgido/pe...     Alezio     NaN   
...                                                   ...        ...     ...   
994773  https://www.miodottore.it/elena-mazzola/dermat...    Palermo     5.0   
994774  https://www.miodottore.it/roberta-alaimo/derma...    Palermo     5.0   
994775  https://www.miodottore.it/ninfa-alessandra-gia...    Palermo     5.0   
994776  https://www.miodottore.it/francesca-todaro-3/d...    Palermo     5.0   
994777  https://www.miodottore.it/maria-rita-bongiorno...    Palermo     5.0   

       number_of_reviews                                        prestazioni  \
0                    NaN                                                 {}   
1                    NaN                                                 {}   
2                    NaN                                                 {}   
3                    NaN                                                 {}   
4                    NaN                                                 {}   
...                  ...                                                ...   
994773        Recensioni  {"Visita dermatologica": "100 €", "Crioterapia...   
994774        Recensioni  {"Prima visita dermatologica": "Da 70 €", "Inf...   
994775        Recensioni  {"Visita urologica": null, "Visita di controll...   
994776        Recensioni  {"Prima visita dermatologica": "100 €", "Visit...   
994777        Recensioni  {"Visita dermatologica": "220 €", "Visita a do...   

                                              espierienze    prefix  
0                                                      {}       Dr.  
1                                                      {}       Dr.  
2                                                      {}    Angela  
3                                                      {}     Dott.  
4                                                      {}       Dr.  
...                                                   ...       ...  
994773  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa  
994774  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa  
994775  {"expertIn": ["Andrologia", "Urologia", "Medic...  Dott.ssa  
994776  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa  
994777  {"expertIn": ["Dermatologia e venereologia"], ...  Prof.ssa  

[994778 rows x 9 columns]

In [5]:
# Check prefixes
df_prefix = df_cleaned_1['prefix'].unique() # Check unique prefixes in the prefix column
# Check if the prefix is in the list of prefixes
prefixes = ['Dr.', 'Dott.', 'Prof.', 'Prof.ssa', 'Dott.ssa', 'Dottor.', 'Dottore', 'Dottoressa']
df_cleaned_1['is_prefix'] = df_cleaned_1['prefix'].isin(prefixes)  # Create a new column to check if the prefix is in the list
df_cleaned_1


/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/943951686.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_1['is_prefix'] = df_cleaned_1['prefix'].isin(prefixes)  # Create a new column to check if the prefix is in the list


name                               categories  \
0                      Antonio Iasi                             ["Pediatra"]   
1                Piera Angela Negro                             ["Pediatra"]   
2                            Russo                              ["Pediatra"]   
3                    Ivana Stapane                              ["Pediatra"]   
4                Salvatore Fulgido                              ["Pediatra"]   
...                             ...                                      ...   
994773               Elena Mazzola              ["Dermatologo, Venereologo"]   
994774              Roberta Alaimo   ["Dermatologo, Venereologo, Tricologo"]   
994775  Ninfa Alessandra Giacalone       ["Urologo, Andrologo, Venereologo"]   
994776            Francesca Todaro              ["Dermatologo, Venereologo"]   
994777        Maria Rita Bongiorno              ["Dermatologo, Venereologo"]   

                                                      url   location  rating  \
0       https://www.miodottore.it/antonio-iasi/pediatr...    Neviano     NaN   
1       https://www.miodottore.it/piera-angela-negro/p...  Gallipoli     NaN   
2       https://www.miodottore.it/angela-russo-2/pedia...   Galatone     NaN   
3       https://www.miodottore.it/ivana-stapane/pediat...   Galatone     NaN   
4       https://www.miodottore.it/salvatore-fulgido/pe...     Alezio     NaN   
...                                                   ...        ...     ...   
994773  https://www.miodottore.it/elena-mazzola/dermat...    Palermo     5.0   
994774  https://www.miodottore.it/roberta-alaimo/derma...    Palermo     5.0   
994775  https://www.miodottore.it/ninfa-alessandra-gia...    Palermo     5.0   
994776  https://www.miodottore.it/francesca-todaro-3/d...    Palermo     5.0   
994777  https://www.miodottore.it/maria-rita-bongiorno...    Palermo     5.0   

       number_of_reviews                                        prestazioni  \
0                    NaN                                                 {}   
1                    NaN                                                 {}   
2                    NaN                                                 {}   
3                    NaN                                                 {}   
4                    NaN                                                 {}   
...                  ...                                                ...   
994773        Recensioni  {"Visita dermatologica": "100 €", "Crioterapia...   
994774        Recensioni  {"Prima visita dermatologica": "Da 70 €", "Inf...   
994775        Recensioni  {"Visita urologica": null, "Visita di controll...   
994776        Recensioni  {"Prima visita dermatologica": "100 €", "Visit...   
994777        Recensioni  {"Visita dermatologica": "220 €", "Visita a do...   

                                              espierienze    prefix  is_prefix  
0                                                      {}       Dr.       True  
1                                                      {}       Dr.       True  
2                                                      {}    Angela      False  
3                                                      {}     Dott.       True  
4                                                      {}       Dr.       True  
...                                                   ...       ...        ...  
994773  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa       True  
994774  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa       True  
994775  {"expertIn": ["Andrologia", "Urologia", "Medic...  Dott.ssa       True  
994776  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa       True  
994777  {"expertIn": ["Dermatologia e venereologia"], ...  Prof.ssa       True  

[994778 rows x 10 columns]

In [6]:
# Check the rows that have prefix = False
df_no_prefix = df_cleaned_1[df_cleaned_1['is_prefix'] == False]
df_no_prefix

name                    categories  \
2                  Russo                   ["Pediatra"]   
5               Tarantino                  ["Pediatra"]   
7                 Cataldi                  ["Pediatra"]   
8                   Rizzo                  ["Pediatra"]   
30                Pollini                  ["Pediatra"]   
...                   ...                           ...   
993400  Antonella Spurio   ["Dermatologo, Venereologo"]   
993940  Antonella Spurio   ["Dermatologo, Venereologo"]   
994128  Antonella Spurio   ["Dermatologo, Venereologo"]   
994723  Antonella Spurio   ["Dermatologo, Venereologo"]   
994750  Antonella Spurio   ["Dermatologo, Venereologo"]   

                                                      url  location  rating  \
2       https://www.miodottore.it/angela-russo-2/pedia...  Galatone     NaN   
5       https://www.miodottore.it/angelica-tarantino/p...    Tuglie     NaN   
7       https://www.miodottore.it/assunta-cataldi/pedi...    Tuglie     NaN   
8       https://www.miodottore.it/lelio-rizzo/pediatra...  Galatina     NaN   
30      https://www.miodottore.it/sonia-pollini/pediat...      Arco     NaN   
...                                                   ...       ...     ...   
993400  https://www.miodottore.it/maria-antonella-spur...    Vedano     5.0   
993940  https://www.miodottore.it/maria-antonella-spur...    Vedano     5.0   
994128  https://www.miodottore.it/maria-antonella-spur...    Vedano     5.0   
994723  https://www.miodottore.it/maria-antonella-spur...    Vedano     5.0   
994750  https://www.miodottore.it/maria-antonella-spur...    Vedano     5.0   

       number_of_reviews                                        prestazioni  \
2                    NaN                                                 {}   
5                    NaN                                                 {}   
7                    NaN                                                 {}   
8                    NaN                                                 {}   
30                   NaN                                                 {}   
...                  ...                                                ...   
993400        Recensioni  {"Visita dermatologica": "Da 140 €", "Asportaz...   
993940        Recensioni  {"Visita dermatologica": "Da 140 €", "Asportaz...   
994128        Recensioni  {"Visita dermatologica": "Da 140 €", "Asportaz...   
994723        Recensioni  {"Visita dermatologica": "Da 140 €", "Asportaz...   
994750        Recensioni  {"Visita dermatologica": "Da 140 €", "Asportaz...   

                                              espierienze    prefix  is_prefix  
2                                                      {}    Angela      False  
5                                                      {}  Angelica      False  
7                                                      {}   Assunta      False  
8                                                      {}     Lelio      False  
30                                                     {}     Sonia      False  
...                                                   ...       ...        ...  
993400  {"expertIn": ["Dermatologia e venereologia", "...     Maria      False  
993940  {"expertIn": ["Dermatologia e venereologia", "...     Maria      False  
994128  {"expertIn": ["Dermatologia e venereologia", "...     Maria      False  
994723  {"expertIn": ["Dermatologia e venereologia", "...     Maria      False  
994750  {"expertIn": ["Dermatologia e venereologia", "...     Maria      False  

[72840 rows x 10 columns]

In [7]:
# For thr rows that have prefix = False, we realize that it's a first name not prefix so we will add it back to the name column
df_cleaned_1.loc[df_cleaned_1['is_prefix'] == False, 'name'] = df_cleaned_1['prefix'] + ' ' + df_cleaned_1['name']
# Change the prefix to None for these rows using if_else
df_cleaned_1.loc[df_cleaned_1['is_prefix'] == False, 'prefix'] = None
# Check df_cleaned_1
df_cleaned_1

name                               categories  \
0                      Antonio Iasi                             ["Pediatra"]   
1                Piera Angela Negro                             ["Pediatra"]   
2                     Angela Russo                              ["Pediatra"]   
3                    Ivana Stapane                              ["Pediatra"]   
4                Salvatore Fulgido                              ["Pediatra"]   
...                             ...                                      ...   
994773               Elena Mazzola              ["Dermatologo, Venereologo"]   
994774              Roberta Alaimo   ["Dermatologo, Venereologo, Tricologo"]   
994775  Ninfa Alessandra Giacalone       ["Urologo, Andrologo, Venereologo"]   
994776            Francesca Todaro              ["Dermatologo, Venereologo"]   
994777        Maria Rita Bongiorno              ["Dermatologo, Venereologo"]   

                                                      url   location  rating  \
0       https://www.miodottore.it/antonio-iasi/pediatr...    Neviano     NaN   
1       https://www.miodottore.it/piera-angela-negro/p...  Gallipoli     NaN   
2       https://www.miodottore.it/angela-russo-2/pedia...   Galatone     NaN   
3       https://www.miodottore.it/ivana-stapane/pediat...   Galatone     NaN   
4       https://www.miodottore.it/salvatore-fulgido/pe...     Alezio     NaN   
...                                                   ...        ...     ...   
994773  https://www.miodottore.it/elena-mazzola/dermat...    Palermo     5.0   
994774  https://www.miodottore.it/roberta-alaimo/derma...    Palermo     5.0   
994775  https://www.miodottore.it/ninfa-alessandra-gia...    Palermo     5.0   
994776  https://www.miodottore.it/francesca-todaro-3/d...    Palermo     5.0   
994777  https://www.miodottore.it/maria-rita-bongiorno...    Palermo     5.0   

       number_of_reviews                                        prestazioni  \
0                    NaN                                                 {}   
1                    NaN                                                 {}   
2                    NaN                                                 {}   
3                    NaN                                                 {}   
4                    NaN                                                 {}   
...                  ...                                                ...   
994773        Recensioni  {"Visita dermatologica": "100 €", "Crioterapia...   
994774        Recensioni  {"Prima visita dermatologica": "Da 70 €", "Inf...   
994775        Recensioni  {"Visita urologica": null, "Visita di controll...   
994776        Recensioni  {"Prima visita dermatologica": "100 €", "Visit...   
994777        Recensioni  {"Visita dermatologica": "220 €", "Visita a do...   

                                              espierienze    prefix  is_prefix  
0                                                      {}       Dr.       True  
1                                                      {}       Dr.       True  
2                                                      {}      None      False  
3                                                      {}     Dott.       True  
4                                                      {}       Dr.       True  
...                                                   ...       ...        ...  
994773  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa       True  
994774  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa       True  
994775  {"expertIn": ["Andrologia", "Urologia", "Medic...  Dott.ssa       True  
994776  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa       True  
994777  {"expertIn": ["Dermatologia e venereologia"], ...  Prof.ssa       True  

[994778 rows x 10 columns]

In [58]:
# Remove the duplicate rows
df_cleaned_nodup = df_cleaned_1.drop_duplicates(subset=['url'], keep='first', ignore_index=True)
# Check the cleaned dataframe
df_cleaned_nodup

name                    categories  \
0                Antonio Iasi                  ["Pediatra"]   
1          Piera Angela Negro                  ["Pediatra"]   
2               Angela Russo                   ["Pediatra"]   
3              Ivana Stapane                   ["Pediatra"]   
4          Salvatore Fulgido                   ["Pediatra"]   
...                       ...                           ...   
114749      Alice Ramondetta   ["Dermatologo, Venereologo"]   
114750      Francesca Todaro   ["Dermatologo, Venereologo"]   
114751           Luigi Pisano  ["Dermatologo, Venereologo"]   
114752      Adele Sparavigna   ["Dermatologo, Venereologo"]   
114753  Maria Rita Bongiorno   ["Dermatologo, Venereologo"]   

                                                      url   location  rating  \
0       https://www.miodottore.it/antonio-iasi/pediatr...    Neviano     NaN   
1       https://www.miodottore.it/piera-angela-negro/p...  Gallipoli     NaN   
2       https://www.miodottore.it/angela-russo-2/pedia...   Galatone     NaN   
3       https://www.miodottore.it/ivana-stapane/pediat...   Galatone     NaN   
4       https://www.miodottore.it/salvatore-fulgido/pe...     Alezio     NaN   
...                                                   ...        ...     ...   
114749  https://www.miodottore.it/alice-ramondetta/der...    Catania     5.0   
114750  https://www.miodottore.it/francesca-todaro-3/d...    Palermo     5.0   
114751  https://www.miodottore.it/luigi-pisano/dermato...    Firenze     5.0   
114752  https://www.miodottore.it/adele-sparavigna/der...     Milano     5.0   
114753  https://www.miodottore.it/maria-rita-bongiorno...    Palermo     5.0   

       number_of_reviews                                        prestazioni  \
0                    NaN                                                 {}   
1                    NaN                                                 {}   
2                    NaN                                                 {}   
3                    NaN                                                 {}   
4                    NaN                                                 {}   
...                  ...                                                ...   
114749        Recensioni  {"Visita dermatologica": "Da 80 €", "Consulenz...   
114750        Recensioni  {"Prima visita dermatologica": "100 €", "Visit...   
114751        Recensioni                                                 {}   
114752        Recensioni  {"Prima visita dermatologica": "180 €", "Visit...   
114753        Recensioni  {"Visita dermatologica": "220 €", "Visita a do...   

                                              espierienze    prefix  is_prefix  
0                                                      {}       Dr.       True  
1                                                      {}       Dr.       True  
2                                                      {}      None      False  
3                                                      {}     Dott.       True  
4                                                      {}       Dr.       True  
...                                                   ...       ...        ...  
114749  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa       True  
114750  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa       True  
114751  {"expertIn": ["Dermatologia e venereologia"], ...       Dr.       True  
114752  {"expertIn": ["Dermatologia e venereologia", "...  Dott.ssa       True  
114753  {"expertIn": ["Dermatologia e venereologia"], ...  Prof.ssa       True  

[114754 rows x 10 columns]

In [59]:
# Check the final DataFrame
df_cleaned_1['name'].unique().shape  # Check unique names in the name column

# Check is there Maurizio Piani in the name column
maurizio_piani = df_cleaned_nodup[df_cleaned_nodup['name'] == 'Maria Rita Bongiorno ']



In [60]:
maurizio_piani

name                    categories  \
114753  Maria Rita Bongiorno   ["Dermatologo, Venereologo"]   

                                                      url location  rating  \
114753  https://www.miodottore.it/maria-rita-bongiorno...  Palermo     5.0   

       number_of_reviews                                        prestazioni  \
114753        Recensioni  {"Visita dermatologica": "220 €", "Visita a do...   

                                              espierienze    prefix  is_prefix  
114753  {"expertIn": ["Dermatologia e venereologia"], ...  Prof.ssa       True

In [ ]:
# for df_cleaned_1, add a new location_2 by transforming location to province that the location is in
# For example, Milano -> Milano, Neviano -> Lecce, Gallipoli -> Lecce, etc.


Clean and Manage FNOMCEO

In [199]:
# Look up the fnomceo data
df_fnomceo = pd.read_csv('fnomceo-all-data-up-to-4-gen-2023.csv')
df_fnomceo

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/1956483652.py:2: DtypeWarning: Columns (35,36,37,38,39,40,41,43,45,46,47,48,49,50,51,53,54,55,56,58,60,61,62,63,64,65,66,67,68) have mixed types. Specify dtype option on import or set low_memory=False.
  df_fnomceo = pd.read_csv('fnomceo-all-data-up-to-4-gen-2023.csv')


index  fnomceo_id                     name sex   birthdate   age  \
0            0        20.0          Magrini Antonio   M  1953-04-30  69.0   
1            1        21.0       Tamborini Emanuela   F  1963-03-28  59.0   
2            2        22.0        Di Fronzo Antonio   M  1954-06-26  68.0   
3            3        23.0            Ruta Giovanni   M  1960-08-18  62.0   
4            4        24.0      Evangelisti Daniela   F  1955-07-09  67.0   
...        ...         ...                      ...  ..         ...   ...   
552297  552302    614424.0            Ferrari Fabio   M  1997-08-12  25.0   
552298  552303    614425.0             Aresi Nicola   M  1995-12-22  27.0   
552299  552304    614426.0            Pozzoni Elena   F  1997-02-11  25.0   
552300  552305    614427.0  Tresoldi Maria Vittoria   F  1996-02-08  26.0   
552301  552306    614428.0   Faustinelli Alessandro   M  1997-12-16  25.0   

           birthplace birth_province   data_date            profession  \
0               SERRE             SA  2022-12-28           Odontoiatra   
1              VARESE             VA  2023-01-02                Medico   
2         SANT'ANTIMO            NaN  2022-12-23                Medico   
3              MODICA             RG  2022-12-19                Medico   
4            CAMAIORE             LU  2022-11-24  Medico e odontoiatra   
...               ...            ...         ...                   ...   
552297        SERIATE             BG  2023-01-03           Odontoiatra   
552298        BERGAMO             BG  2023-01-03           Odontoiatra   
552299        BRESCIA             BS  2023-01-03                Medico   
552300  VAPRIO D'ADDA             MI  2023-01-03                Medico   
552301        BRESCIA             BS  2023-01-03                Medico   

        is_active physician_qualification_place physician_qualification_date  \
0            True     NAPOLI SECONDA UNIVERSITA                   1982-02-01   
1            True                         PAVIA                   1989-01-01   
2            True                        NAPOLI                   1992-01-01   
3            True                       CATANIA                   1986-02-01   
4            True                          PISA                   1988-01-01   
...           ...                           ...                          ...   
552297       True                           NaN                          NaN   
552298       True                       BRESCIA                   2022-02-01   
552299       True                           NaN                          NaN   
552300       True                           NaN                          NaN   
552301       True                           NaN                          NaN   

       physician_register_place  physician_register_number  \
0                       SALERNO                     5167.0   
1                        VARESE                     4366.0   
2                        NAPOLI                    26132.0   
3                        RAGUSA                     1660.0   
4                         LUCCA                     2003.0   
...                         ...                        ...   
552297                      NaN                        NaN   
552298                      NaN                        NaN   
552299                  BERGAMO                     8543.0   
552300                  BERGAMO                     8542.0   
552301                  BERGAMO                     8544.0   

       physician_register_date  graduations_count  \
0                   1982-12-31                1.0   
1                   1989-06-20                1.0   
2                   1992-06-29                1.0   
3                   1987-01-30                1.0   
4                   1989-06-13                1.0   
...                        ...                ...   
552297                     NaN                1.0   
552298                     NaN                1.0   
552299      

In [201]:
# Check is there Maurizio Piani in the fnomceo data
maurizio_piani_fnomceo = df_fnomceo[df_fnomceo['name'].str.contains('Negro Piera Angela', na=False, case=False)]
maurizio_piani_fnomceo

index  fnomceo_id                name sex   birthdate   age birthplace  \
90504  90505     97432.0  Negro Piera Angela   F  1953-08-19  69.0     VARESE   

      birth_province   data_date profession  is_active  \
90504             VA  2023-01-02     Medico       True   

      physician_qualification_place physician_qualification_date  \
90504                         PAVIA                   1978-02-01   

      physician_register_place  physician_register_number  \
90504                    LECCE                     3382.0   

      physician_register_date  graduations_count graduations_faculty_1  \
90504              1982-01-25                1.0  MEDICINA E CHIRURGIA   

      graduations_date_1 graduations_place_1  residencies_count  \
90504         1978-07-28               PAVIA                1.0   

      residencies_residency_1 residencies_place_1 residencies_date_1  \
90504            PUERICULTURA               PAVIA         1981-07-13   

       special_attributes_count special_attributes_attribute_1  \
90504                       0.0                            NaN   

       special_attributes_date_1 dentist_register_place  \
90504                        NaN                    NaN   

       dentist_register_number dentist_register_date residencies_residency_2  \
90504                      NaN                   NaN                     NaN   

      residencies_place_2 residencies_date_2 dentist_qualification_place  \
90504                 NaN                NaN                         NaN   

      dentist_qualification_date residencies_residency_3 residencies_place_3  \
90504                        NaN                     NaN                 NaN   

      residencies_date_3 residencies_residency_4 residencies_place_4  \
90504                NaN                     NaN                 NaN   

      residencies_date_4 special_attributes_attribute_2  \
90504                NaN                            NaN   

       special_attributes_date_2 special_attributes_attribute_3  \
90504                        NaN                            NaN   

       special_attributes_date_3 residencies_residency_5 residencies_place_5  \
90504                        NaN                     NaN                 NaN   

      residencies_date_5 graduations_faculty_2 graduations_date_2  \
90504                NaN                   NaN                NaN   

      graduations_place_2 special_attributes_attribute_4  \
90504                 NaN                            NaN   

       special_attributes_date_4 residencies_residency_6 residencies_place_6  \
90504                        NaN                     NaN                 NaN   

      residencies_date_6 special_attributes_attribute_5  \
90504                NaN                            NaN   

       special_attributes_date_5 special_attributes_attribute_6  \
90504                        NaN                            NaN   

       special_attributes_date_6 residencies_residency_7 residencies_place_7  \
90504                        NaN                     NaN                 NaN   

      residencies_date_7 residencies_residency_8 residencies_place_8  \
90504                NaN                     NaN                 NaN   

      residencies_date_8 residencies_residency_9 residencies_place_9  \
90504                NaN                     NaN                 NaN   

      residencies_date_9  
90504                NaN

In [202]:
# Check the name in df_fnomceo
df_fnomceo['name'].unique().shape  # Check unique names in the name column

(491188,)

In [203]:
# Lower all the name in fnomeceo
df_fnomceo['name'] = df_fnomceo['name'].str.lower().str.strip()  # Lowercase and strip

In [204]:
# Create a new column in df_cleaned_nodup to count the number of repeated names
df_cleaned_nodup['name_count'] = df_cleaned_nodup.groupby('name')['name'].transform('count')

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/432867408.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup['name_count'] = df_cleaned_nodup.groupby('name')['name'].transform('count')


In [205]:
# Check the rows with name_count 
df_cleaned_nodup.loc[df_cleaned_nodup['name_count'] > 1]  # Show only rows with name_count > 1

name                                    categories  \
9            Ermanno Baldo          ["Allergologo, Immunologo, Pediatra"]   
25          Sofia Pallante   ["Pediatra, Omeopata, Medico certificatore"]   
26          Luigi Palmieri                      ["Pediatra, Allergologo"]   
168          Vincenzo Rosa             ["Agopuntore, Omeopata, Pediatra"]   
201       Luigi Di Lorenzo                                   ["Pediatra"]   
...                     ...                                           ...   
114591     Carlo Marchetti                                    ["Urologo"]   
114607      Antonio Romano                                    ["Urologo"]   
114725  Giuseppe Benincasa                                    ["Urologo"]   
114735    Maurizio Colombo                                    ["Urologo"]   
114748     Giuseppe Quarta                   ["Dermatologo, Venereologo"]   

                                                      url   location  rating  \
9       https://www.miodottore.it/ermanno-baldo/allerg...       Riva     5.0   
25      https://www.miodottore.it/sofia-pallante/pedia...       Roma     5.0   
26      https://www.miodottore.it/luigi-palmieri/pedia...       Bari     5.0   
168     https://www.miodottore.it/vincenzo-rosa-3/pedi...    Canneto     NaN   
201     https://www.miodottore.it/luigi-di-lorenzo-2/p...     Napoli     5.0   
...                                                   ...        ...     ...   
114591  https://www.miodottore.it/carlo-marchetti-2/ur...      Pavia     5.0   
114607  https://www.miodottore.it/antonio-romano-13/ur...      Piove     5.0   
114725  https://www.miodottore.it/giuseppe-benincasa/u...      Vallo     NaN   
114735  https://www.miodottore.it/maurizio-colombo-2/u...  Villanova     5.0   
114748  https://www.miodottore.it/giuseppe-quarta-4/de...      Lecce     NaN   

       number_of_reviews                                        prestazioni  \
9             Recensioni  {"Prima visita allergologica": "120 €", "Prima...   
25            Recensioni  {"Consulenza online": "35 €", "Prima visita pe...   
26            Recensioni  {"Prima visita pediatrica": "85 €", "Visita pn...   
168                  NaN  {"Prima visita pediatrica": "60 € - 100 €", "O...   
201           Recensioni  {"Visita pediatrica": null, "Bilancio di salut...   
...                  ...                                                ...   
114591        Recensioni  {"Prima visita urologica": "120 €", "Visita ur...   
114607        Recensioni  {"Prima visita urologica": "140 €", "Uroflusso...   
114725               NaN                                                 {}   
114735        Recensioni                      {"Visita urologica": "130 €"}   
114748               NaN                            {"Dermatoscopia": null}   

                                              espierienze    prefix  \
9       {"expertIn": ["Allergologia e immunologia clin...     Dott.   
25      {"expertIn": ["Omeopatia", "Omotossicologia", ...  Dott.ssa   
26      {"expertIn": ["Allergologia e immunologia clin...     Dott.   
168     {"expertIn": ["Medicina olistica", "Medicina f...     Dott.   
201     {"disease": ["Disturbi Della Crescita", "Asma"...       Dr.   
...                                                   ...       ...   
114591  {"expertIn": ["Urologia"], "disease": ["Carcin...       Dr.   
114607                                                 {}     Dott.   
114725                                                 {}      None   
114735                                                 {}     Dott.   
114748  {"expertIn": ["Dermatologia e venereologia"], ...     Dott.   

        is_prefix  name_count  
9            True           2  
25           True           2  
26           True           2  
168          True           2  
201          True           2  
...           ...         ...  
114591       True           2  
114607       True           2  
114725      False           2  
114735       Tr

In [206]:
# Divide the data into two parts, one with name_count > 1 and one with name_count = 1
df_cleaned_nodup_count_gt_1 = df_cleaned_nodup[df_cleaned_nodup['name_count'] > 1]
df_cleaned_nodup_count_eq_1 = df_cleaned_nodup[df_cleaned_nodup['name_count'] == 1]

In [207]:
# Modify the name column in df_cleaned_nodup_count_eq_1 by lowering the case of the name and also remove all the spaces at the end
df_cleaned_nodup_count_eq_1['name'] = df_cleaned_nodup_count_eq_1['name'].str.lower().str.strip()  # Lowercase and stripdf
df_cleaned_nodup_count_gt_1['name'] = df_cleaned_nodup_count_gt_1['name'].str.lower().str.strip()  # Lowercase and stripdf

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/4092890731.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup_count_eq_1['name'] = df_cleaned_nodup_count_eq_1['name'].str.lower().str.strip()  # Lowercase and stripdf
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/4092890731.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup_count_gt_1['name'] = df_cleaned_nodup_count_gt_1['name'].str.lower().str.strip()  # Lowercase and stripdf


In [208]:
# Change the pattern name in df_cleaned_nodup_count_eq_1 to match the name in df_fnomceo
parts = df_cleaned_nodup_count_eq_1['name'].str.split(' ')
df_cleaned_nodup_count_eq_1['first_name'] = parts.apply(lambda x: " ".join(x[:-1]))  # Combine first two parts as name
df_cleaned_nodup_count_eq_1['last_name'] = parts.apply(lambda x: x[-1])  # Last part as last name

# Rejoin the first and last name to form the new name column
df_cleaned_nodup_count_eq_1['new_name'] = df_cleaned_nodup_count_eq_1['last_name'] + ' ' + df_cleaned_nodup_count_eq_1['first_name']
df_cleaned_nodup_count_eq_1

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/142318713.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup_count_eq_1['first_name'] = parts.apply(lambda x: " ".join(x[:-1]))  # Combine first two parts as name
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/142318713.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup_count_eq_1['last_name'] = parts.apply(lambda x: x[-1])  # Last part as last name
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0

name                    categories  \
0               antonio iasi                  ["Pediatra"]   
1         piera angela negro                  ["Pediatra"]   
2               angela russo                  ["Pediatra"]   
3              ivana stapane                  ["Pediatra"]   
4          salvatore fulgido                  ["Pediatra"]   
...                      ...                           ...   
114749      alice ramondetta  ["Dermatologo, Venereologo"]   
114750      francesca todaro  ["Dermatologo, Venereologo"]   
114751          luigi pisano  ["Dermatologo, Venereologo"]   
114752      adele sparavigna  ["Dermatologo, Venereologo"]   
114753  maria rita bongiorno  ["Dermatologo, Venereologo"]   

                                                      url   location  rating  \
0       https://www.miodottore.it/antonio-iasi/pediatr...    Neviano     NaN   
1       https://www.miodottore.it/piera-angela-negro/p...  Gallipoli     NaN   
2       https://www.miodottore.it/angela-russo-2/pedia...   Galatone     NaN   
3       https://www.miodottore.it/ivana-stapane/pediat...   Galatone     NaN   
4       https://www.miodottore.it/salvatore-fulgido/pe...     Alezio     NaN   
...                                                   ...        ...     ...   
114749  https://www.miodottore.it/alice-ramondetta/der...    Catania     5.0   
114750  https://www.miodottore.it/francesca-todaro-3/d...    Palermo     5.0   
114751  https://www.miodottore.it/luigi-pisano/dermato...    Firenze     5.0   
114752  https://www.miodottore.it/adele-sparavigna/der...     Milano     5.0   
114753  https://www.miodottore.it/maria-rita-bongiorno...    Palermo     5.0   

       number_of_reviews                                        prestazioni  \
0                    NaN                                                 {}   
1                    NaN                                                 {}   
2                    NaN                                                 {}   
3                    NaN                                                 {}   
4                    NaN                                                 {}   
...                  ...                                                ...   
114749        Recensioni  {"Visita dermatologica": "Da 80 €", "Consulenz...   
114750        Recensioni  {"Prima visita dermatologica": "100 €", "Visit...   
114751        Recensioni                                                 {}   
114752        Recensioni  {"Prima visita dermatologica": "180 €", "Visit...   
114753        Recensioni  {"Visita dermatologica": "220 €", "Visita a do...   

                                              espierienze    prefix  \
0                                                      {}       Dr.   
1                                                      {}       Dr.   
2                                                      {}      None   
3                                                      {}     Dott.   
4                                                      {}       Dr.   
...                                                   ...       ...   
114749  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa   
114750  {"expertIn": ["Dermatologia e venereologia"], ...  Dott.ssa   
114751  {"expertIn": ["Dermatologia e venereologia"], ...       Dr.   
114752  {"expertIn": ["Dermatologia e venereologia", "...  Dott.ssa   
114753  {"expertIn": ["Dermatologia e venereologia"], ...  Prof.ssa   

        is_prefix  name_count    first_name   last_name              new_name  
0            True           1       antonio        iasi          iasi antonio  
1            True           1  piera angela       negro    negro piera angela  
2           False           1        angela       russo          russo angela  
3            True           1         ivana     stapane         stapane ivana  
4            True           1     salvatore     fulgido     fulgido salvatore  
...           ...         ...       

In [209]:
# Change the pattern name in df_cleaned_nodup_count_gt_1 to match the name in df_fnomceo
parts = df_cleaned_nodup_count_gt_1['name'].str.split(' ')
df_cleaned_nodup_count_gt_1['first_name'] = parts.apply(lambda x: " ".join(x[:-1]))  # Combine first two parts as name
df_cleaned_nodup_count_gt_1['last_name'] = parts.apply(lambda x: x[-1])  # Last part as last name

# Rejoin the first and last name to form the new name column
df_cleaned_nodup_count_gt_1['new_name'] = df_cleaned_nodup_count_gt_1['last_name'] + ' ' + df_cleaned_nodup_count_gt_1['first_name']
df_cleaned_nodup_count_gt_1.head()

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/1511968787.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup_count_gt_1['first_name'] = parts.apply(lambda x: " ".join(x[:-1]))  # Combine first two parts as name
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/1511968787.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup_count_gt_1['last_name'] = parts.apply(lambda x: x[-1])  # Last part as last name
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6

name                                    categories  \
9       ermanno baldo         ["Allergologo, Immunologo, Pediatra"]   
25     sofia pallante  ["Pediatra, Omeopata, Medico certificatore"]   
26     luigi palmieri                     ["Pediatra, Allergologo"]   
168     vincenzo rosa            ["Agopuntore, Omeopata, Pediatra"]   
201  luigi di lorenzo                                  ["Pediatra"]   

                                                   url location  rating  \
9    https://www.miodottore.it/ermanno-baldo/allerg...     Riva     5.0   
25   https://www.miodottore.it/sofia-pallante/pedia...     Roma     5.0   
26   https://www.miodottore.it/luigi-palmieri/pedia...     Bari     5.0   
168  https://www.miodottore.it/vincenzo-rosa-3/pedi...  Canneto     NaN   
201  https://www.miodottore.it/luigi-di-lorenzo-2/p...   Napoli     5.0   

    number_of_reviews                                        prestazioni  \
9          Recensioni  {"Prima visita allergologica": "120 €", "Prima...   
25         Recensioni  {"Consulenza online": "35 €", "Prima visita pe...   
26         Recensioni  {"Prima visita pediatrica": "85 €", "Visita pn...   
168               NaN  {"Prima visita pediatrica": "60 € - 100 €", "O...   
201        Recensioni  {"Visita pediatrica": null, "Bilancio di salut...   

                                           espierienze    prefix  is_prefix  \
9    {"expertIn": ["Allergologia e immunologia clin...     Dott.       True   
25   {"expertIn": ["Omeopatia", "Omotossicologia", ...  Dott.ssa       True   
26   {"expertIn": ["Allergologia e immunologia clin...     Dott.       True   
168  {"expertIn": ["Medicina olistica", "Medicina f...     Dott.       True   
201  {"disease": ["Disturbi Della Crescita", "Asma"...       Dr.       True   

     name_count first_name last_name          new_name  
9             2    ermanno     baldo     baldo ermanno  
25            2      sofia  pallante    pallante sofia  
26            2      luigi  palmieri    palmieri luigi  
168           2   vincenzo      rosa     rosa vincenzo  
201           2   luigi di   lorenzo  lorenzo luigi di

Try Ollama LLM

In [210]:
# Install ollama
!pip install ollama

In [211]:
# Add the province column to location by using ollama
import ollama
from functools import lru_cache

# Model name
model_name = 'mistral'

# Optional: open log file (uncomment if you want file logging)
# log_file = open("province_extraction_log.txt", "w")

@lru_cache(maxsize=None)
def extract_province_of_commune(commune):
    """
    Extracts the Italian province for a given commune using an LLM via Ollama.
    Uses caching to avoid duplicate LLM calls.
    """
    prompt = (
        "Extract the province of Italy from the following commune name:\n"
        "For example, if the commune is 'Milano', the province is 'Milano'. "
        "If the commune is 'Neviano', the province is 'Lecce'.\n"
        "Just return the Italian province name. No explanation.\n"
        "Write the province name in Italian (e.g., Genova, Napoli, Roma).\n"
        "No full sentences, no parentheses, just the name.\n"
        f"Description: {commune}"
    )

    response = ollama.chat(
        model=model_name,
        messages=[{'role': 'user', 'content': prompt}]
    )

    raw_text = response['message']['content'].splitlines()[0].strip().upper()

    # Optional: log to file instead of printing
    # log_file.write(f"{commune} → {raw_text}\n")
    # log_file.flush()

    return raw_text




Merge a province name based on the commune name, using georef dataset (Already cleaned)

In [212]:
# Read the commune_province CSV file
commune_province = pd.read_csv('georef-italy-comune 2.csv')

# check the commune_province dataframe
commune_province['Official Name Comune']

# Merge a province name based on the commune name, using georef dataset (Already cleaned)
df_cleaned_nodup_count_eq_1 = pd.merge(
    df_cleaned_nodup_count_eq_1,
    commune_province[['Official Name Comune', 'Official Name Provincia/Città metropolitana']],
    left_on='location',
    right_on='Official Name Comune',
    how='left')

df_cleaned_nodup_count_gt_1 = pd.merge(
    df_cleaned_nodup_count_gt_1,
    commune_province[['Official Name Comune', 'Official Name Provincia/Città metropolitana']],
    left_on='location',
    right_on='Official Name Comune',
    how='left')

In [213]:
# Making province name column all uppercase
df_cleaned_nodup_count_eq_1['Official Name Provincia/Città metropolitana'] = df_cleaned_nodup_count_eq_1['Official Name Provincia/Città metropolitana'].str.upper()
df_cleaned_nodup_count_gt_1['Official Name Provincia/Città metropolitana'] = df_cleaned_nodup_count_gt_1['Official Name Provincia/Città metropolitana'].str.upper()

In [214]:
# Check the rows that have NaN in the province name column
df_cleaned_nodup_count_eq_1_Na = df_cleaned_nodup_count_eq_1[df_cleaned_nodup_count_eq_1['Official Name Provincia/Città metropolitana'].isna()]
df_cleaned_nodup_count_gt_1_Na = df_cleaned_nodup_count_gt_1[df_cleaned_nodup_count_gt_1['Official Name Provincia/Città metropolitana'].isna()]
df_cleaned_nodup_count_eq_1_not_Na = df_cleaned_nodup_count_eq_1[df_cleaned_nodup_count_eq_1['Official Name Provincia/Città metropolitana'].notna()]
df_cleaned_nodup_count_gt_1_not_Na = df_cleaned_nodup_count_gt_1[df_cleaned_nodup_count_gt_1['Official Name Provincia/Città metropolitana'].notna()]

from tqdm import tqdm

# Drop missing and get unique commune names
unique_communes = df_cleaned_nodup_count_eq_1_Na['location'].dropna().unique()

# Build a mapping
commune_to_province = {comm: extract_province_of_commune(comm) for comm in tqdm(unique_communes)}

# Apply the map to the DataFrame
df_cleaned_nodup_count_eq_1_Na['Official Name Provincia/Città metropolitana'] = df_cleaned_nodup_count_eq_1_Na['location'].map(commune_to_province)


100%|██████████| 1484/1484 [26:17<00:00,  1.06s/it] 
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/2789709729.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup_count_eq_1_Na['Official Name Provincia/Città metropolitana'] = df_cleaned_nodup_count_eq_1_Na['location'].map(commune_to_province)


In [215]:
from tqdm import tqdm

# Drop missing and get unique commune names
unique_communes = df_cleaned_nodup_count_gt_1_Na['location'].dropna().unique()

# Build a mapping
commune_to_province = {comm: extract_province_of_commune(comm) for comm in tqdm(unique_communes)}

# Apply the map to the DataFrame
df_cleaned_nodup_count_gt_1_Na['Official Name Provincia/Città metropolitana'] = df_cleaned_nodup_count_gt_1_Na['location'].map(commune_to_province)


100%|██████████| 264/264 [00:10<00:00, 24.51it/s]
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/2494831353.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_cleaned_nodup_count_gt_1_Na['Official Name Provincia/Città metropolitana'] = df_cleaned_nodup_count_gt_1_Na['location'].map(commune_to_province)


In [216]:
df_cleaned_nodup_count_gt_1_Na

name                                         categories  \
0          ermanno baldo              ["Allergologo, Immunologo, Pediatra"]   
3          vincenzo rosa                 ["Agopuntore, Omeopata, Pediatra"]   
13     giuseppe recupero                                       ["Pediatra"]   
28      gaetano quaranta  ["Pediatra di Libera Scelta, Allergologo, Pedi...   
31          paola rocchi                                       ["Pediatra"]   
...                  ...                                                ...   
3695     giuseppe romano                                        ["Urologo"]   
3697     giuseppe marino                                        ["Urologo"]   
3703      antonio romano                                        ["Urologo"]   
3704  giuseppe benincasa                                        ["Urologo"]   
3705    maurizio colombo                                        ["Urologo"]   

                                                    url    location  rating  \
0     https://www.miodottore.it/ermanno-baldo/allerg...        Riva     5.0   
3     https://www.miodottore.it/vincenzo-rosa-3/pedi...     Canneto     NaN   
13    https://www.miodottore.it/giuseppe-recupero/pe...  Barcellona     NaN   
28    https://www.miodottore.it/gaetano-quaranta-2/p...  Piedimonte     5.0   
31    https://www.miodottore.it/paola-rocchi-2/pedia...     Caldana     5.0   
...                                                 ...         ...     ...   
3695  https://www.miodottore.it/giuseppe-romano-15/u...        Vibo     NaN   
3697  https://www.miodottore.it/giuseppe-marino-14/u...      Mazara     NaN   
3703  https://www.miodottore.it/antonio-romano-13/ur...       Piove     5.0   
3704  https://www.miodottore.it/giuseppe-benincasa/u...       Vallo     NaN   
3705  https://www.miodottore.it/maurizio-colombo-2/u...   Villanova     5.0   

     number_of_reviews                                        prestazioni  \
0           Recensioni  {"Prima visita allergologica": "120 €", "Prima...   
3                  NaN  {"Prima visita pediatrica": "60 € - 100 €", "O...   
13                 NaN                                                 {}   
28          Recensioni  {"Visita pediatrica": "60 €", "Visita allergol...   
31          Recensioni                                                 {}   
...                ...                                                ...   
3695               NaN                         {"Visita urologica": null}   
3697               NaN      {"Visita urologica": null, "Ecografia": null}   
3703        Recensioni  {"Prima visita urologica": "140 €", "Uroflusso...   
3704               NaN                                                 {}   
3705        Recensioni                      {"Visita urologica": "130 €"}   

                                            espierienze prefix  is_prefix  \
0     {"expertIn": ["Allergologia e immunologia clin...  Dott.       True   
3     {"expertIn": ["Medicina olistica", "Medicina f...  Dott.       True   
13                                                   {}    Dr.       True   
28    {"disease": ["Asma", "Eczema", "Tonsillite", "...    Dr.       True   
31                                                   {}    Dr.       True   
...                                                 ...    ...        ...   
3695  {"expertIn": ["Urologia"], "disease": ["Cistit...    Dr.       True   
3697  {"expertIn": ["Urologia"], "disease": ["Colica...   None      False   
3703                                                 {}  Dott.       True   
3704                                                 {}   None      False   
3705                                                 {}  Dott.       True   

      name_count first_name  last_name            new_name  \
0              2    ermanno      baldo       baldo ermanno   
3              2   vincenzo       rosa       rosa vincenzo   
13             2   giuseppe   recupero   recupero giuseppe   
28             3    gaet

In [217]:
# Concatenate the two dataframes back together
df_cleaned_nodup_count_eq_1 = pd.concat([df_cleaned_nodup_count_eq_1_not_Na, df_cleaned_nodup_count_eq_1_Na], ignore_index=True)

In [218]:
# Concatenate the two dataframes back together
df_cleaned_nodup_count_gt_1 = pd.concat([df_cleaned_nodup_count_gt_1_not_Na, df_cleaned_nodup_count_gt_1_Na], ignore_index=True)

FNOMCEO Management and Cleaning (2)

In [221]:
# Split df_fnomceo
df_fnomceo['name_count'] = df_fnomceo.groupby('name')['name'].transform('count')

In [222]:
# Get all columns displayed (max columns)
pd.set_option('display.max_columns', None)
df_fnomceo['physician_register_place']

0         SALERNO
1          VARESE
2          NAPOLI
3          RAGUSA
4           LUCCA
           ...   
552297        NaN
552298        NaN
552299    BERGAMO
552300    BERGAMO
552301    BERGAMO
Name: physician_register_place, Length: 552302, dtype: object

In [223]:
# If df_fnomceo do not have physician_register_place, then we will use the dentist_register_place
df_fnomceo['physician_register_place'] = df_fnomceo['physician_register_place'].fillna(df_fnomceo['dentist_register_place'])

In [224]:
# Divide the data into two parts, one with name_count > 1 and one with name_count = 1
df_fnomceo_count_gt_1 = df_fnomceo[df_fnomceo['name_count'] > 1]
df_fnomceo_count_eq_1 = df_fnomceo[df_fnomceo['name_count'] == 1]

In [225]:
# Merge the df_cleaned_nodup_count_eq_1 and df_fnomceo_count_eq_1 on the name column
df_merged_1 = pd.merge(df_cleaned_nodup_count_eq_1, df_fnomceo_count_eq_1, left_on='new_name', right_on= 'name', how='inner')
# Merge the df_cleaned_nodup_count_eq_1 and df_fnomceo_gt_1 on the name column and matched location
df_merged_2 = pd.merge(df_cleaned_nodup_count_eq_1, df_fnomceo_count_gt_1, 
                       left_on=['new_name', 'Official Name Provincia/Città metropolitana'],
                       right_on=['name', 'physician_register_place'],
                       how='inner')
# Merge the df_cleaned_nodup_count_gt_1 and df_fnomceo on the name column and matched location
df_merged_3 = pd.merge(df_cleaned_nodup_count_gt_1, df_fnomceo_count_eq_1,
                       left_on=['new_name', 'Official Name Provincia/Città metropolitana'],
                       right_on=['name', 'physician_register_place'],
                       how='inner')
df_merged_4 = pd.merge(df_cleaned_nodup_count_gt_1, df_fnomceo_count_gt_1,
                       left_on=['new_name', 'Official Name Provincia/Città metropolitana'],
                       right_on=['name', 'physician_register_place'],
                       how='inner')

In [227]:
# Look at the df_merged_1 and df_merged_2 again but this time change how to left to see the rows that are not matched
df_merged_1_left = pd.merge(df_cleaned_nodup_count_eq_1, df_fnomceo_count_eq_1, left_on='new_name', right_on='name', how='left')
df_merged_2_left = pd.merge(df_cleaned_nodup_count_eq_1, df_fnomceo_count_gt_1,
                            left_on=['new_name', 'Official Name Provincia/Città metropolitana'],
                            right_on=['name', 'physician_register_place'],
                            how='left')

In [234]:
# Observe df_merged_1_left
df_unmatched_name = df_merged_1_left[df_merged_1_left['name_y'].notna()]  # Show only rows where name is NaN

- Some people have middle name in fnomceo but not from the miodottore website, so we need to merge them based on the first name and last name
- sometimes name has ', for example ali', so we need to remove it

In [235]:
# Recall the df_fnomceo_eq_1 and re-clean it again
# Consider these 41170 rows in fnomceo_eq_1 
name_matched = [name for name in df_unmatched_name['new_name'].unique()]
df_fnomceo_count_eq_1_unmatched_name = df_fnomceo_count_eq_1[df_fnomceo_count_eq_1['name'].isin(name_matched) == False]
df_fnomceo_count_eq_1_unmatched_name

index  fnomceo_id                                     name sex  \
1            1        21.0                       tamborini emanuela   F   
2            2        22.0                        di fronzo antonio   M   
3            3        23.0                            ruta giovanni   M   
5            5        25.0                          fiocca federico   M   
8            8        28.0  coggi berzetti di buronzo giorgio paolo   M   
...        ...         ...                                      ...  ..   
552294  552299    614421.0                        caracausi antonio   M   
552296  552301    614423.0                       berbenni christian   M   
552298  552303    614425.0                             aresi nicola   M   
552299  552304    614426.0                            pozzoni elena   F   
552301  552306    614428.0                   faustinelli alessandro   M   

         birthdate   age   birthplace birth_province   data_date   profession  \
1       1963-03-28  59.0       VARESE             VA  2023-01-02       Medico   
2       1954-06-26  68.0  SANT'ANTIMO            NaN  2022-12-23       Medico   
3       1960-08-18  62.0       MODICA             RG  2022-12-19       Medico   
5       1975-12-25  47.0       VERONA             VR  2022-12-29       Medico   
8       1953-12-12  69.0       TORINO             TO  2022-12-29       Medico   
...            ...   ...          ...            ...         ...          ...   
552294  1991-04-28  31.0        BARGA             LU  2023-01-03  Odontoiatra   
552296  1992-09-27  30.0      SEGRATE             MI  2023-01-03  Odontoiatra   
552298  1995-12-22  27.0      BERGAMO             BG  2023-01-03  Odontoiatra   
552299  1997-02-11  25.0      BRESCIA             BS  2023-01-03       Medico   
552301  1997-12-16  25.0      BRESCIA             BS  2023-01-03       Medico   

        is_active physician_qualification_place physician_qualification_date  \
1            True                         PAVIA                   1989-01-01   
2            True                        NAPOLI                   1992-01-01   
3            True                       CATANIA                   1986-02-01   
5            True                        VERONA                   2002-01-01   
8            True                        TORINO                   1979-02-01   
...           ...                           ...                          ...   
552294       True                           NaN                          NaN   
552296       True                           NaN                          NaN   
552298       True                       BRESCIA                   2022-02-01   
552299       True                           NaN                          NaN   
552301       True                           NaN                          NaN   

       physician_register_place  physician_register_number  \
1                        VARESE                     4366.0   
2                        NAPOLI                    26132.0   
3                        RAGUSA                     1660.0   
5                        VERONA                     7174.0   
8                        TORINO                    10648.0   
...                         ...                        ...   
552294                    LUCCA                        NaN   
552296                  BERGAMO                        NaN   
552298                  BERGAMO                        NaN   
552299                  BERGAMO                     8543.0   
552301                  BERGAMO                     8544.0   

       physician_register_date  graduations_count  \
1                   1989-06-20                1.0   
2                   1992-06-29                1.0   
3                   1987-01-30                1.0   
5                   2002-09-02                1.0   
8                   1980-01-29                1.0   
...                        ...                ...   
552294                     NaN                1.0   
55229

In [239]:
# We will clean this by cut everything in the name that is not a letter or a space
df_fnomceo_count_eq_1_unmatched_name['name'] = df_fnomceo_count_eq_1_unmatched_name['name'].str.replace(r'[^a-zA-Z\s]', '', regex=True)
# Lowercase the name
df_fnomceo_count_eq_1_unmatched_name['name'] = df_fnomceo_count_eq_1_unmatched_name['name'].str.lower().str.strip()  # Lowercase and strip
# Remove all the spaces at the end
df_fnomceo_count_eq_1_unmatched_name['name'] = df_fnomceo_count_eq_1_unmatched_name['name'].str.strip()  # Strip spaces

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/2882368564.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_fnomceo_count_eq_1_unmatched_name['name'] = df_fnomceo_count_eq_1_unmatched_name['name'].str.replace(r'[^a-zA-Z\s]', '', regex=True)
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/2882368564.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_fnomceo_count_eq_1_unmatched_name['name'] = df_fnomceo_count_eq_1_unmatched_name['name'].str.lower().str.strip()  # L

In [241]:
# We will merge this to create df_merged_5
df_merged_5 = pd.merge(df_cleaned_nodup_count_eq_1, df_fnomceo_count_eq_1_unmatched_name,
                       left_on='new_name',
                       right_on='name',
                       how='inner')
df_merged_5

name_x  \
0                sergio sano   
1               bruno romano   
2    nicolo salvatore titone   
3                walter orru   
4             francesco luca   
..                       ...   
107             valchiria do   
108    maria concetta giofre   
109       domenico paternico   
110              andrea coli   
111     mohammad ali chaouaf   

                                            categories  \
0                                         ["Pediatra"]   
1                               ["Pediatra, Omeopata"]   
2    ["Pneumologo, Internista, Medico di medicina g...   
3                       ["Psicoterapeuta, Psichiatra"]   
4     ["Psicologo, Psicoterapeuta, Psicologo clinico"]   
..                                                 ...   
107                                     ["Cardiologo"]   
108                                     ["Cardiologo"]   
109                              ["Chirurgo generale"]   
110                                      ["Terapeuta"]   
111                                        ["Urologo"]   

                                                   url  location  rating  \
0    https://www.miodottore.it/sergio-sano/pediatra...   Cartura     NaN   
1    https://www.miodottore.it/bruno-romano-4/pedia...      Roma     5.0   
2    https://www.miodottore.it/nicolo-salvatore-tit...    Alcamo     NaN   
3    https://www.miodottore.it/walter-orru/psicoter...   Bergamo     5.0   
4    https://www.miodottore.it/francesco-luca/psico...    Azzate     5.0   
..                                                 ...       ...     ...   
107  https://www.miodottore.it/valchiria-do/cardiol...  Castello     NaN   
108  https://www.miodottore.it/maria-concetta-giofr...    Reggio     NaN   
109  https://www.miodottore.it/domenico-paternico/c...  Cernusco     NaN   
110  https://www.miodottore.it/andrea-coli/terapeut...       San     5.0   
111  https://www.miodottore.it/mohammad-ali-chaouaf...    Quinto     NaN   

    number_of_reviews                                        prestazioni  \
0                 NaN                                                 {}   
1          Recensioni  {"Prima visita omeopatica": "140 €", "Prima vi...   
2                 NaN                                                 {}   
3          Recensioni  {"Visita psichiatrica": "120 €", "Ciclo di psi...   
4          Recensioni  {"Colloquio psicologico": "63 €", "Colloquio p...   
..                ...                                                ...   
107               NaN                                                 {}   
108               NaN  {"Consulenza online": "50 €", "Visita cardiolo...   
109               NaN                                                 {}   
110        Recensioni  {"Laser terapia": "20 €", "Tecar terapia": "40...   
111               NaN                                                 {}   

                                           espierienze    prefix  is_prefix  \
0                                                   {}      None      False   
1    {"expertIn": ["Omeopatia"], "disease": ["Distu...       Dr.       True   
2                                                   {}       Dr.       True   
3    {"expertIn": ["Psicoterapia"], "disease": ["An...       Dr.       True   
4    {"expertIn": ["Psicoterapia", "Psiconcologia",...     Dott.       True   
..                                                 ...       ...        ...   
107                                                 {}       Dr.       True   
108  {"expertIn": ["Medicina interna"], "disease": ...  Dott.ssa       True   
109                                                 {}     Dott.       True   
110  {"disease": ["Cervicalgia", "Disturbi del movi...     Dott.       True   
111                                                 {}       Dr.       True   

     name_count_x        first_name  last_name                 new_name  \
0               1            sergio       sano              sano sergio   
1              

In [247]:
# Next, we will clean the df_fnomceo_count_gt_1_unmatched_name again by delete the middle name 
# Cut the last chunk of the name after the last space
df_fnomceo_count_eq_1_unmatched_name_2 = df_fnomceo_count_eq_1_unmatched_name.copy()
df_fnomceo_count_eq_1_unmatched_name_2['name'] = df_fnomceo_count_eq_1_unmatched_name['name'].str.split(' ').str[:-1].str.join(' ')

In [253]:
# Create df_merged_6 by merging df_cleaned_nodup_count_gt_1 and df_fnomceo_count_eq_1_unmatched_name_2
df_merged_6 = pd.merge(df_cleaned_nodup_count_gt_1, df_fnomceo_count_eq_1_unmatched_name_2,
                       left_on='new_name',
                       right_on='name',
                       how='inner')

In [255]:
df_merged_6.drop_duplicates(subset=['name_x'], keep='first', inplace=True)  # Remove duplicates based on URL
df_merged_6

name_x                                         categories  \
0           marco greco                                       ["Pediatra"]   
2        giuseppe leone                                       ["Pediatra"]   
4     giuseppe esposito            ["Pediatra di Libera Scelta, Pediatra"]   
5       vincenzo caruso                                       ["Pediatra"]   
8         marta ferrari           ["Pediatra, Endocrinologo, Diabetologo"]   
...                 ...                                                ...   
1118     giovanni rizzo                             ["Medico dello sport"]   
1138    michele cavallo  ["Medico estetico, Medico di medicina generale...   
1147     antonio romano                    ["Gastroenterologo, Epatologo"]   
1171      elisa colombo                                  ["Nutrizionista"]   
1181    giovanni iacono                                       ["Oculista"]   

                                                    url    location  rating  \
0     https://www.miodottore.it/marco-greco/pediatra...     Firenze     5.0   
2     https://www.miodottore.it/giuseppe-leone-8/ped...    Barletta     NaN   
4     https://www.miodottore.it/giuseppe-esposito-10...     Bedonia     NaN   
5     https://www.miodottore.it/vincenzo-caruso-4/pe...   Benevento     5.0   
8     https://www.miodottore.it/marta-ferrari-5/pedi...     Firenze     5.0   
...                                                 ...         ...     ...   
1118  https://www.miodottore.it/giovanni-rizzo-5/med...     Cellino     4.5   
1138  https://www.miodottore.it/michele-cavallo-3/me...      Marano     5.0   
1147  https://www.miodottore.it/antonio-romano-3/gas...         San     5.0   
1171  https://www.miodottore.it/elisa-colombo-5/nutr...     Paderno     5.0   
1181  https://www.miodottore.it/giovanni-iacono-8/oc...  Civitanova     5.0   

     number_of_reviews                                        prestazioni  \
0           Recensioni  {"Visita pediatrica": "80 €", "Visita a domici...   
2                  NaN                                                 {}   
4                  NaN  {"Prima visita pediatrica": null, "Visita per ...   
5           Recensioni                                                 {}   
8           Recensioni  {"Prima visita endocrinologica": "100 €", "Pri...   
...                ...                                                ...   
1118              30.0  {"Visita Medico Sportiva": null, "Visita medic...   
1138              63.0  {"Visita medica generica in CONVENZIONE": "Da ...   
1147              10.0  {"Prima visita gastroenterologica": "200 €", "...   
1171        Recensioni  {"Prima visita nutrizionale": "120 €", "Prima ...   
1181        Recensioni  {"Visita oculistica completa + fondo oculare":...   

                                            espierienze    prefix  is_prefix  \
0     {"disease": ["Faringite", "Otite", "Convulsion...       Dr.       True   
2                                                    {}      None      False   
4     {"school": ["Laurea in Medicina e Chirurgia pr...       Dr.       True   
5                                                    {}      None      False   
8     {"disease": ["Obesità", "Sovrappeso", "Diabete...  Dott.ssa       True   
...                                                 ...       ...        ...   
1118  {"disease": ["Contrattura", "Articolazione", "...       Dr.       True   
1138  {"expertIn": ["Medicina generale"], "disease":...       Dr.       True   
1147  {"expertIn": ["Gastroenterologia"], "disease":...       Dr.       True   
1171  {"expertIn": ["Scienze dell'alimentazione uman...  Dott.ssa       True   
1181  {"expertIn": ["Oftalmologia"], "disease": ["Ca...     Dott.       True   

      name_count_x first_name last_name           new_name  \
0                2      marco     greco        greco marco   
2                2   giuseppe     leone     leone giuseppe   
4                4   giuseppe  esposito  esposito giuseppe 

In [ ]:
# Sanity check (1)
df_merged_2_ab = pd.merge(df_cleaned_nodup_count_eq_1, df_fnomceo_count_gt_1,
                          left_on= 'new_name',
                          right_on='name',
                            how='inner')
df_merged_2_ab.drop_duplicates(subset=['name_x'], keep='first', inplace=True)  # Remove duplicates based on URL
df_merged_2_ab

name_x                               categories  \
0               angela russo                             ["Pediatra"]   
7        marco maria mariani                ["Pediatra, Allergologo"]   
9      maria grazia giuliani                             ["Pediatra"]   
13        michela giovannini  ["Pediatra di Libera Scelta, Pediatra"]   
15            felice perillo                             ["Pediatra"]   
...                      ...                                      ...   
22214         gennaro romano                              ["Urologo"]   
22216         antonio florio                              ["Urologo"]   
22218        pierpaolo manca                   ["Andrologo, Urologo"]   
22220        michele gentile                              ["Urologo"]   
22225       maurizio ranieri                              ["Urologo"]   

                                                     url    location  rating  \
0      https://www.miodottore.it/angela-russo-2/pedia...    Galatone     NaN   
7      https://www.miodottore.it/marco-maria-mariani-...      Arezzo     3.5   
9      https://www.miodottore.it/maria-grazia-giulian...         Rho     NaN   
13     https://www.miodottore.it/michela-giovannini/p...     Argenta     NaN   
15     https://www.miodottore.it/felice-perillo/pedia...  Marigliano     5.0   
...                                                  ...         ...     ...   
22214  https://www.miodottore.it/gennaro-romano/urolo...   Giugliano     NaN   
22216  https://www.miodottore.it/antonio-florio/urolo...         San     NaN   
22218  https://www.miodottore.it/pierpaolo-manca-2/an...      Quartu     NaN   
22220  https://www.miodottore.it/michele-gentile/urol...     Rionero     NaN   
22225  https://www.miodottore.it/maurizio-ranieri/uro...      Aquila     NaN   

      number_of_reviews                                        prestazioni  \
0                   NaN                                                 {}   
7            Recensioni  {"Visita pediatrica": "Da 80 €", "Visita aller...   
9                   NaN  {"Visita pediatrica": null, "Boel test": null,...   
13                  NaN  {"Prima visita pediatrica": null, "Visita pedi...   
15           Recensioni  {"Visita pediatrica": null, "Boel test": null,...   
...                 ...                                                ...   
22214               NaN                         {"Visita urologica": null}   
22216               NaN                                                 {}   
22218               NaN                                                 {}   
22220               NaN                                                 {}   
22225               NaN                                                 {}   

                                             espierienze    prefix  is_prefix  \
0                                                     {}      None      False   
7      {"disease": ["Disturbi Della Crescita", "Eczem...      None      False   
9      {"disease": ["Disturbi Della Crescita", "Asma"...       Dr.       True   
13                                                    {}  Dott.ssa       True   
15     {"disease": ["Disturbi Della Crescita", "Asma"...      None      False   
...                                                  ...       ...        ...   
22214                                                 {}     Prof.       True   
22216                                                 {}      None      False   
22218                                                 {}      None      False   
22220                                                 {}       Dr.       True   
22225                                                 {}      None      False   

       name_count_x    first_name   last_name               new_name  \
0                 1        angela       russo           russo angela   
7                 1   marco maria     mariani    mariani marco maria   
9                 1  maria grazia    giuliani  giuliani ma

In [ ]:
# Now observe df_merged_2_left
df_unmatched_name_2 = df_merged_2_left[df_merged_2_left['name_y'].notna()]  # Show only rows where name is NaN
df_unmatched_name_2 

name_x                 categories  \
2                angela russo               ["Pediatra"]   
30        marco maria mariani  ["Pediatra, Allergologo"]   
61      maria grazia giuliani               ["Pediatra"]   
62      maria grazia giuliani               ["Pediatra"]   
103            felice perillo               ["Pediatra"]   
...                       ...                        ...   
111348     francesco muratore              ["Radiologo"]   
111763        pierpaolo manca     ["Andrologo, Urologo"]   
111777        michele gentile                ["Urologo"]   
111791       maurizio ranieri                ["Urologo"]   
111792       maurizio ranieri                ["Urologo"]   

                                                      url    location  rating  \
2       https://www.miodottore.it/angela-russo-2/pedia...    Galatone     NaN   
30      https://www.miodottore.it/marco-maria-mariani-...      Arezzo     3.5   
61      https://www.miodottore.it/maria-grazia-giulian...         Rho     NaN   
62      https://www.miodottore.it/maria-grazia-giulian...         Rho     NaN   
103     https://www.miodottore.it/felice-perillo/pedia...  Marigliano     5.0   
...                                                   ...         ...     ...   
111348  https://www.miodottore.it/francesco-muratore-2...      Misano     NaN   
111763  https://www.miodottore.it/pierpaolo-manca-2/an...      Quartu     NaN   
111777  https://www.miodottore.it/michele-gentile/urol...     Rionero     NaN   
111791  https://www.miodottore.it/maurizio-ranieri/uro...      Aquila     NaN   
111792  https://www.miodottore.it/maurizio-ranieri/uro...      Aquila     NaN   

       number_of_reviews                                        prestazioni  \
2                    NaN                                                 {}   
30            Recensioni  {"Visita pediatrica": "Da 80 €", "Visita aller...   
61                   NaN  {"Visita pediatrica": null, "Boel test": null,...   
62                   NaN  {"Visita pediatrica": null, "Boel test": null,...   
103           Recensioni  {"Visita pediatrica": null, "Boel test": null,...   
...                  ...                                                ...   
111348               NaN                                {"Ecografia": null}   
111763               NaN                                                 {}   
111777               NaN                                                 {}   
111791               NaN                                                 {}   
111792               NaN                                                 {}   

                                              espierienze prefix  is_prefix  \
2                                                      {}   None      False   
30      {"disease": ["Disturbi Della Crescita", "Eczem...   None      False   
61      {"disease": ["Disturbi Della Crescita", "Asma"...    Dr.       True   
62      {"disease": ["Disturbi Della Crescita", "Asma"...    Dr.       True   
103     {"disease": ["Disturbi Della Crescita", "Asma"...   None      False   
...                                                   ...    ...        ...   
111348                                                 {}  Dott.       True   
111763                                                 {}   None      False   
111777                                                 {}    Dr.       True   
111791                                                 {}   None      False   
111792                                                 {}   None      False   

        name_count_x    first_name last_name               new_name  \
2                  1        angela     russo           russo angela   
30                 1   marco maria   mariani    mariani marco maria   
61                 1  maria grazia  giuliani  giuliani maria grazia   
62                 1  maria grazia  giuliani  giuliani maria grazia   
103                1        felice   perillo         perillo felice   
...  

In [260]:
# Recall the df_fnomceo_eq_1 and re-clean it again

name_matched_2 = [name for name in df_unmatched_name_2['new_name'].unique()]
df_fnomceo_count_gt_1_unmatched_name = df_fnomceo_count_gt_1[df_fnomceo_count_gt_1['name'].isin(name_matched_2) == False]
df_fnomceo_count_gt_1_unmatched_name

index  fnomceo_id                 name sex   birthdate   age  \
0            0        20.0      magrini antonio   M  1953-04-30  69.0   
4            4        24.0  evangelisti daniela   F  1955-07-09  67.0   
6            6        26.0    quaranta giovanni   M  1964-10-09  58.0   
7            7        27.0      villani valeria   F  1955-07-20  67.0   
15          15        36.0       montanari enzo   M  1973-07-31  49.0   
...        ...         ...                  ...  ..         ...   ...   
552286  552291    614413.0         erba stefano   M  1996-05-09  26.0   
552287  552292    614414.0     fenu maria laura   F  1993-01-20  29.0   
552293  552298    614420.0  carcangiu giampaolo   M  1958-06-11  64.0   
552295  552300    614422.0     santilli daniele   M  1997-08-28  25.0   
552297  552302    614424.0        ferrari fabio   M  1997-08-12  25.0   

                birthplace birth_province   data_date            profession  \
0                    SERRE             SA  2022-12-28           Odontoiatra   
4                 CAMAIORE             LU  2022-11-24  Medico e odontoiatra   
6                   TORINO             TO  2022-12-29                Medico   
7                  BOLOGNA             BO  2022-12-30                Medico   
15      REGGIO NELL'EMILIA             RE  2023-01-02                Medico   
...                    ...            ...         ...                   ...   
552286       BUSTO ARSIZIO             VA  2023-01-02                Medico   
552287            CAGLIARI             CA  2023-01-02                Medico   
552293            CAGLIARI             CA  2023-01-03                Medico   
552295             ISERNIA             IS  2023-01-03                Medico   
552297             SERIATE             BG  2023-01-03           Odontoiatra   

        is_active   physician_qualification_place  \
0            True       NAPOLI SECONDA UNIVERSITA   
4            True                            PISA   
6            True                          TORINO   
7            True  BOLOGNA "ALMA MATER STUDIORUM"   
15           True          MODENA E REGGIO EMILIA   
...           ...                             ...   
552286       True                        CAGLIARI   
552287       True                        CAGLIARI   
552293       True                           PAVIA   
552295       True                             NaN   
552297       True                             NaN   

       physician_qualification_date physician_register_place  \
0                        1982-02-01                  SALERNO   
4                        1988-01-01                    LUCCA   
6                        1991-02-01                   TORINO   
7                        1980-02-01                  BOLOGNA   
15                       2003-01-01            REGGIO EMILIA   
...                             ...                      ...   
552286                   2022-01-01                 CAGLIARI   
552287                   2022-02-01                 CAGLIARI   
552293                   1985-01-01                 CAGLIARI   
552295                          NaN                  ISERNIA   
552297                          NaN                  BERGAMO   

        physician_register_number physician_register_date  graduations_count  \
0                          5167.0              1982-12-31                1.0   
4                          2003.0              1989-06-13                1.0   
6                         16019.0              1991-05-29                1.0   
7                          8785.0              1980-12-16                1.0   
15                         3148.0              2003-07-15                1.0   
...                           ...                     ...                ...   
552286                    11332.0              2022-12-13                1.0   
552287                    11333.0              2022-12-13                1.0   
552293                     4936.0              1985-06-26

In [261]:
# We will clean this by cut everything in the name that is not a letter or a space
df_fnomceo_count_gt_1_unmatched_name['name'] = df_fnomceo_count_gt_1_unmatched_name['name'].str.replace(r'[^a-zA-Z\s]', '', regex=True)
# Lowercase the name
df_fnomceo_count_gt_1_unmatched_name['name'] = df_fnomceo_count_gt_1_unmatched_name['name'].str.lower().str.strip()  # Lowercase and strip
# Remove all the spaces at the end
df_fnomceo_count_gt_1_unmatched_name['name'] = df_fnomceo_count_gt_1_unmatched_name['name'].str.strip()  # Strip spaces

/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/3175462003.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_fnomceo_count_gt_1_unmatched_name['name'] = df_fnomceo_count_gt_1_unmatched_name['name'].str.replace(r'[^a-zA-Z\s]', '', regex=True)
/var/folders/90/cwb_ycfx3g1cp7q2t1rv6g6m0000gn/T/ipykernel_99385/3175462003.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_fnomceo_count_gt_1_unmatched_name['name'] = df_fnomceo_count_gt_1_unmatched_name['name'].str.lower().str.strip()  # L

In [267]:
# We will merge this to create df_merged_7
df_merged_7 = pd.merge(df_cleaned_nodup_count_eq_1, df_fnomceo_count_gt_1_unmatched_name,
                       left_on=['new_name', 'Official Name Provincia/Città metropolitana'],
                       right_on=['name', 'physician_register_place'],
                       how='inner')
df_merged_7

name_x                                   categories  \
0        anna calio  ["Internista, Medico di medicina generale"]   
1     giuseppe orru                        ["Medico competente"]   
2     roberto secli        ["Anestesista, Terapista del dolore"]   
3  francesco ferrau                                 ["Oncologo"]   

                                                 url          location  \
0  https://www.miodottore.it/anna-calio/internist...           Marsala   
1  https://www.miodottore.it/giuseppe-orru-2/medi...  Cavallermaggiore   
2  https://www.miodottore.it/roberto-secli-2/anes...           Bologna   
3  https://www.miodottore.it/francesco-ferrau/onc...         Zafferana   

   rating number_of_reviews  \
0     NaN               NaN   
1     NaN               NaN   
2     5.0               7.0   
3     5.0        Recensioni   

                                         prestazioni  \
0                                                 {}   
1                                                 {}   
2  {"Consulenza online": "100 €", "Prima visita d...   
3               {"Prima visita oncologica": "250 €"}   

                                         espierienze prefix  is_prefix  \
0                                                 {}    Dr.       True   
1                                                 {}   None      False   
2  {"expertIn": ["Anestesia rianimazione, terapia...  Dott.       True   
3                                                 {}  Dott.       True   

   name_count_x first_name last_name          new_name Official Name Comune  \
0             1       anna     calio        calio anna              Marsala   
1             1   giuseppe      orru     orru giuseppe     Cavallermaggiore   
2             1    roberto     secli     secli roberto              Bologna   
3             1  francesco    ferrau  ferrau francesco                  NaN   

  Official Name Provincia/Città metropolitana   index  fnomceo_id  \
0                                     TRAPANI   63568     68461.0   
1                                       CUNEO  189592    203892.0   
2                                     BOLOGNA  423362    477421.0   
3                                     CATANIA  349445    375907.0   

             name_y sex   birthdate   age                 birthplace  \
0        calio anna   F  1955-04-08  67.0  SANTA CATERINA VILLARMOSA   
1     orru giuseppe   M  1965-07-09  57.0                    TRAPANI   
2     secli roberto   M  1981-05-18  41.0                   GALATINA   
3  ferrau francesco   M  1959-08-05  63.0                    CATANIA   

  birth_province   data_date profession  is_active  \
0             CL  2022-12-22     Medico       True   
1             TP  2022-12-30     Medico       True   
2             LE  2022-12-30     Medico       True   
3             CT  2022-12-30     Medico       True   

    physician_qualification_place physician_qualification_date  \
0                         PALERMO                   1983-01-01   
1                         PALERMO                   1991-02-01   
2  BOLOGNA "ALMA MATER STUDIORUM"                   2009-02-01   
3                         CATANIA                   1983-02-01   

  physician_register_place  physician_register_number physician_register_date  \
0                  TRAPANI                     1800.0              1983-06-20   
1                    CUNEO                     4893.0              2019-08-22   
2                  BOLOGNA                    17589.0              2016-03-18   
3                  CATANIA                     7640.0              1984-03-15   

   graduations_count graduations_faculty_1 graduations_date_1  \
0                1.0  MEDICINA E CHIRURGIA         1982-11-09   
1                1.0  MEDICINA E CHIRURGIA         1991-11-08   
2                1.0  MEDICINA E CHIRURGIA         2009-07-20   
3                1.0  MEDICINA E CHIRURGIA         1983-11-10   

              graduations_place_1  residencies_count res

In [268]:
# Concatenate the all dataframes back together
df_final = pd.concat([df_merged_1, df_merged_2, df_merged_3, df_merged_4, df_merged_5, df_merged_6, df_merged_7], ignore_index=True)

In [289]:
df_final

name_x                                   categories  \
0            antonio iasi                                 ["Pediatra"]   
1      piera angela negro                                 ["Pediatra"]   
2           ivana stapane                                 ["Pediatra"]   
3       salvatore fulgido                                 ["Pediatra"]   
4      angelica tarantino                                 ["Pediatra"]   
...                   ...                                          ...   
77369     giovanni iacono                                 ["Oculista"]   
77370          anna calio  ["Internista, Medico di medicina generale"]   
77371       giuseppe orru                        ["Medico competente"]   
77372       roberto secli        ["Anestesista, Terapista del dolore"]   
77373    francesco ferrau                                 ["Oncologo"]   

                                                     url          location  \
0      https://www.miodottore.it/antonio-iasi/pediatr...           Neviano   
1      https://www.miodottore.it/piera-angela-negro/p...         Gallipoli   
2      https://www.miodottore.it/ivana-stapane/pediat...          Galatone   
3      https://www.miodottore.it/salvatore-fulgido/pe...            Alezio   
4      https://www.miodottore.it/angelica-tarantino/p...            Tuglie   
...                                                  ...               ...   
77369  https://www.miodottore.it/giovanni-iacono-8/oc...        Civitanova   
77370  https://www.miodottore.it/anna-calio/internist...           Marsala   
77371  https://www.miodottore.it/giuseppe-orru-2/medi...  Cavallermaggiore   
77372  https://www.miodottore.it/roberto-secli-2/anes...           Bologna   
77373  https://www.miodottore.it/francesco-ferrau/onc...         Zafferana   

       rating number_of_reviews  \
0         NaN               NaN   
1         NaN               NaN   
2         NaN               NaN   
3         NaN               NaN   
4         NaN               NaN   
...       ...               ...   
77369     5.0        Recensioni   
77370     NaN               NaN   
77371     NaN               NaN   
77372     5.0               7.0   
77373     5.0        Recensioni   

                                             prestazioni  \
0                                                     {}   
1                                                     {}   
2                                                     {}   
3                                                     {}   
4                                                     {}   
...                                                  ...   
77369  {"Visita oculistica completa + fondo oculare":...   
77370                                                 {}   
77371                                                 {}   
77372  {"Consulenza online": "100 €", "Prima visita d...   
77373               {"Prima visita oncologica": "250 €"}   

                                             espierienze prefix  is_prefix  \
0                                                     {}    Dr.       True   
1                                                     {}    Dr.       True   
2                                                     {}  Dott.       True   
3                                                     {}    Dr.       True   
4                                                     {}   None      False   
...                                                  ...    ...        ...   
77369  {"expertIn": ["Oftalmologia"], "disease": ["Ca...  Dott.       True   
77370                                                 {}    Dr.       True   
77371                                                 {}   None      False   
77372  {"expertIn": ["Anestesia rianimazione, terapia...  Dott.       True   
77373                                                 {}  Dott.       True   

       name_count_x    first_name  last_name            new_name  \
0                 1       antonio       iasi  

In [290]:
# Save the merged DataFrame to a CSV file
df_final.to_csv("doctor_details_merged_final.csv", index=False)